# Capstone project final Assignment: Battle of Neighborhoods

## New York City vs Toronto vs Paris

### For week #1, you will required to submit the following:

### <font color=blue> A description of the problem and a discussion of the background. (15 marks) </font>



<font color=black> **>** Compare the neighborhoods of the three multicultural cities and determine how similar or dissimilar they are. Is New York City more like Toronto or Paris? <br> **>** Discover the cities and their neigborhoods for planning travel</font> 

### <font color=blue>A description of the data and how it will be used to solve the problem. (15 marks)</font>

<font color=black> **(1)** The data for the three cities include neighborhoods, Borough, Geographical Latitude and Longitude; Foursquare is used for exploring cities and neighborhoods. <br> *>>* **New York City:** 'newyork_data.json' downloaded from  https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json  <br> *>>* **Toronto:** url 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M' and 'Geospatial_Coordinates.csv' <br> *>>* **Paris:** correspondances-code-insee-code-postal.json downloaded from https://www.data.gouv.fr/fr/datasets/r/e88c6fda-1d09-42a0-a069-606d3259114e <br>

**(2)** Data Analysis:<br> *>>* Wrangler the data of the neighborhood data with Pandas Dataframe <br>*>>*  Explore neighborhoods with Foursqure <br> *>>* Visualize using folium map rendering library <br> *>>* Combine data of all three cities for clustering analysis <br> *>>* Cluster and segmentation the neighborhoods of all the three cities together using K-Means method <br> *>>* Examine the cluster and show the similarities/disimilarities</font> 

### For week #2, the final deliverables of the project will be:

1. A link to your Notebook on your Github repository, showing your code. (15 marks)
2. A full report consisting of all of the following components (15 marks): <br>
  *a. Introduction where you discuss the business problem and who would be interested in this project. <br>
  b. Data where you describe the data that will be used to solve the problem and the source of the data. <br>
  c. Methodology section which represents the main component of the report where you discuss and describe any exploratory data analysis that you did, any inferential statistical testing that you performed, if any, and what machine learnings were used and why. <br>
  d. Results section where you discuss the results. <br>
  e. Discussion section where you discuss any observations you noted and any recommendations you can make based on the results. <br>
  d. Conclusion section where you conclude the report. <br>*
3. Your choice of a presentation or blogpost. (10 marks)

# 1: Toronto: 

## 1.1 Data wranglering with BeautifulSoup

In [1]:
!pip install bs4
#!pip install requests

In [2]:
from bs4 import BeautifulSoup 
import requests 
import pandas as pd

In [3]:
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
url

'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'

In [4]:
# get the contents of the webpage in text format and store in a variable called data
data  = requests.get(url).text

In [5]:
soup = BeautifulSoup(data,"html5lib")

#### Webscraping Updated Table
 After retreiving the URL and creating a Beautiful soup object <br>
 Firstly create a list <br>
 Later after finding the table and table data  create a dictionary called cell having 3 keys PostalCode, Borough and Neighborhood.<br>
 As postal code contains upto 3 characters extract that using tablerow.p.text<br>
 Next use split ,strip and replace functions for getting Borough and Neighborhood information.<br>
 Append to the list  <br>
 Create a dataframe with list

In [6]:
## Sample code
table_contents=[]
table=soup.find('table')
len(table)
#pd.read_html(str(table), flavor='bs4')

2

In [7]:
for row in table.findAll('td'):
    cell = {}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['PostalCode'] = row.p.text[:3]
        cell['Borough'] = (row.span.text).split('(')[0]
        cell['Neighborhood'] = (((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
        table_contents.append(cell)

# print(table_contents)
df=pd.DataFrame(table_contents)
#'''
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})
#'''
#df= df.groupby(['PostalCode'], as_index = False).agg({'Borough': ' '.join,'Neighborhood': ' '.join})

In [8]:
#df=df.sort_values(by=['PostalCode'], ascending=True)
df.head(10)
#df.tail(15)
#df

PostalCode           Borough                      Neighborhood
0        M3A        North York                         Parkwoods
1        M4A        North York                  Victoria Village
2        M5A  Downtown Toronto         Regent Park, Harbourfront
3        M6A        North York  Lawrence Manor, Lawrence Heights
4        M7A      Queen's Park     Ontario Provincial Government
5        M9A         Etobicoke                  Islington Avenue
6        M1B       Scarborough                    Malvern, Rouge
7        M3B        North York                   Don Mills North
8        M4B         East York   Parkview Hill, Woodbine Gardens
9        M5B  Downtown Toronto          Garden District, Ryerson

In [9]:
df.shape

(103, 3)

## 1.2 Get the latitude and the longitude coordinates of each neighborhood using the Geocoder package

In [10]:
#read in CSV file downloaded to local 
df_lat_lng = pd.read_csv('Geospatial_Coordinates.csv')
df_latlng = df_lat_lng.rename(columns={"Postal Code": "PostalCode"})
#df_latlng

In [11]:
#join dataframe 
#df_geo = df.set_index('PostalCode').join(lat_lng.set_index('Postal Code'))
df_geo = df.join(df_latlng.set_index('PostalCode'), on='PostalCode')
df_geo

PostalCode                Borough  \
0          M3A             North York   
1          M4A             North York   
2          M5A       Downtown Toronto   
3          M6A             North York   
4          M7A           Queen's Park   
..         ...                    ...   
98         M8X              Etobicoke   
99         M4Y       Downtown Toronto   
100        M7Y  East Toronto Business   
101        M8Y              Etobicoke   
102        M8Z              Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4                        Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100                                     Enclave of M4L  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

In [12]:
#check Lat, Lng for PostalCode 'M5G'
df_geo.loc[df_geo['PostalCode'] == 'M5G', ['Latitude','Longitude']]

Latitude  Longitude
24  43.657952 -79.387383

In [13]:
df_geo.shape

(103, 5)

## 1.3 Explore and cluster the neighborhoods in Toronto

In [14]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
%pip install folium
import folium # map rendering library

print('Libraries imported.')

Note: you may need to restart the kernel to use updated packages.
Libraries imported.


In [15]:
df_Toronto_neighborhood = df_geo
# create map of Toronto using latitude and longitude values
latitude = 43.654260
longitude = -79.360636
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_Toronto_neighborhood['Latitude'], df_Toronto_neighborhood['Longitude'], df_Toronto_neighborhood['Borough'], df_Toronto_neighborhood['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='darkblue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### 1.3.1 segment and cluster all the neighborhoods in all Borough in Toronto

In [16]:
#Slice the original dataframe and create a new dataframe of the toronto_data.
#toronto_data = df_Toronto_neighborhood[df_Toronto_neighborhood['Borough'].str.contains('Toronto')].reset_index(drop=True)
toronto_data = df_Toronto_neighborhood
toronto_data.head()

PostalCode           Borough                      Neighborhood   Latitude  \
0        M3A        North York                         Parkwoods  43.753259   
1        M4A        North York                  Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4        M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

#### 1.3.1.1 Visulaize all neighborhoods of Borough

In [17]:
# create map of Toronto using latitude and longitude values
latitude = 43.654260
longitude = -79.360636
map_toronto_B = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_data['Latitude'], toronto_data['Longitude'], toronto_data['Borough'], toronto_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='skyblue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto_B)  
    
map_toronto_B

#### 3.1.2 Define Foursquare Credentials and Version

In [18]:
CLIENT_ID = '1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5' # your Foursquare ID
CLIENT_SECRET = 'MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE' # your Foursquare Secret
VERSION = '20210404' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5
CLIENT_SECRET:MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE


#### 3.1.3 explore the all neighborhoods

create a function to repeat the same process to all the neighborhoods used from lab

In [19]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id=1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5&client_secret=MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE&v=20210403&ll=40.87655077879964, -73.91065965862981&radius=500&limit=100'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

###### Now write the code to run the above function on each neighborhood and create a new dataframe called _toronto_venues_.

In [20]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighborhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude'])

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Don Mills North
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
The Danforth  East
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmount Park
Bayview Village
Downsview East
The Danforth

###### check the size of this new dataframe

In [21]:
print(toronto_venues.shape)
toronto_venues.head()

(2369, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Parkwoods              43.753259              -79.329656   
1    Parkwoods              43.753259              -79.329656   
2    Parkwoods              43.753259              -79.329656   
3    Parkwoods              43.753259              -79.329656   
4    Parkwoods              43.753259              -79.329656   

                              Venue  Venue Latitude  Venue Longitude  \
0                          Arturo's       40.874412       -73.910271   
1                       Bikram Yoga       40.876844       -73.906204   
2                     Tibbett Diner       40.880404       -73.908937   
3  Astral Fitness & Wellness Center       40.876705       -73.906372   
4                           Dunkin'       40.877136       -73.906666   

  Venue Category  
0    Pizza Place  
1    Yoga Studio  
2          Diner  
3            Gym  
4     Donut Shop

###### check venues by neighborhoods

In [22]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                              23   
Alderwood, Long Branch                                                 23   
Bathurst Manor, Wilson Heights, Downsview North                        23   
Bayview Village                                                        23   
Bedford Park, Lawrence Manor East                                      23   
Berczy Park                                                            23   
Birch Cliff, Cliffside West                                            23   
Brockton, Parkdale Village, Exhibition Place                           23   
CN Tower, King and Spadina, Railway Lands, Harb...                     23   
Caledonia-Fairbanks                                                    23   
Cedarbrae                                                              23   
Central Bay Street                                                     23   
Christie                                                               23   
Church and Wellesley                                                   23   
Clairville, Humberwood, Woodbine Downs, West Hu...                     23   
Clarks Corners, Tam O'Shanter, Sullivan                                23   
Cliffside, Cliffcrest, Scarborough Village West                        23   
Commerce Court, Victoria Hotel                                         23   
Davisville                                                             23   
Davisville North                                                       23   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                       23   
Don Mills North                                                        23   
Don Mills South                                                        23   
Dorset Park, Wexford Heights, Scarborough Town ...                     23   
Downsview Central                                                      23   
Downsview East                                                         23   
Downsview Northwest                                                    23   
Downsview West                                                         23   
Dufferin, Dovercourt Village                                           23   
Enclave of L4W                                                         23   
Enclave of M4L                                                         23   
Enclave of M5E                                                         23   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                     23   
Fairview, Henry Farm, Oriole                                           23   
First Canadian Place, Underground city                                 23   
Forest Hill North & West                                               23   
Garden District, Ryerson                                               23   
Glencairn                                                              23   
Golden Mile, Clairlea, Oakridge                                        23   
Guildwood, Morningside, West Hill                                      23   
Harbourfront East, Union Station, Toronto Islands                      23   
High Park, The Junction South                                          23   
Hillcrest Village                                                      23   
Humber Summit                                                          23   
Humberlea, Emery                                                       23   
Humewood-Cedarvale                                                     23   
India Bazaar, The Beaches West                                         23   
Islington Avenue                                                       23   
Kennedy Park, Ionview, East Birchmount Park                            23   
Kensington Market, Chinatown, Grange Park                              23   
Kingsview Village, St. Phillips, Martin Grove G.

###### check out unique catagories:

In [23]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 21 uniques categories.


### 3.1.4.A Analyze neighborhoods:

In [24]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighborhood  American Restaurant  Clothing Store  Coffee Shop  \
0    Parkwoods                    0               0            0   
1    Parkwoods                    0               0            0   
2    Parkwoods                    0               0            0   
3    Parkwoods                    0               0            0   
4    Parkwoods                    0               0            0   

   Deli / Bodega  Department Store  Diner  Discount Store  Donut Shop  Gym  \
0              0                 0      0               0           0    0   
1              0                 0      0               0           0    0   
2              0                 0      1               0           0    0   
3              0                 0      0               0           0    1   
4              0                 0      0               0           1    0   

   Ice Cream Shop  Kids Store  Pharmacy  Pizza Place  Sandwich Place  \
0               0           0         0            1               0   
1               0           0         0            0               0   
2               0           0         0            0               0   
3               0           0         0            0               0   
4               0           0         0            0               0   

   Seafood Restaurant  Shopping Mall  Steakhouse  Supplement Shop  \
0                   0              0           0                0   
1                   0              0           0                0   
2                   0              0           0                0   
3                   0              0           0                0   
4                   0              0           0                0   

   Tennis Stadium  Video Game Store  Yoga Studio  
0               0                 0            0  
1               0                 0            1  
2               0                 0            0  
3               0                 0            0  
4               0                 0            0

In [25]:
toronto_onehot.shape

(2369, 22)

###### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category



In [26]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  American Restaurant  \
0                                            Agincourt             0.043478   
1                               Alderwood, Long Branch             0.043478   
2      Bathurst Manor, Wilson Heights, Downsview North             0.043478   
3                                      Bayview Village             0.043478   
4                    Bedford Park, Lawrence Manor East             0.043478   
5                                          Berczy Park             0.043478   
6                          Birch Cliff, Cliffside West             0.043478   
7         Brockton, Parkdale Village, Exhibition Place             0.043478   
8    CN Tower, King and Spadina, Railway Lands, Har...             0.043478   
9                                  Caledonia-Fairbanks             0.043478   
10                                           Cedarbrae             0.043478   
11                                  Central Bay Street             0.043478   
12                                            Christie             0.043478   
13                                Church and Wellesley             0.043478   
14   Clairville, Humberwood, Woodbine Downs, West H...             0.043478   
15             Clarks Corners, Tam O'Shanter, Sullivan             0.043478   
16     Cliffside, Cliffcrest, Scarborough Village West             0.043478   
17                      Commerce Court, Victoria Hotel             0.043478   
18                                          Davisville             0.043478   
19                                    Davisville North             0.043478   
20    Del Ray, Mount Dennis, Keelsdale and Silverthorn             0.043478   
21                                     Don Mills North             0.043478   
22                                     Don Mills South             0.043478   
23   Dorset Park, Wexford Heights, Scarborough Town...             0.043478   
24                                   Downsview Central             0.043478   
25                                      Downsview East             0.043478   
26                                 Downsview Northwest             0.043478   
27                                      Downsview West             0.043478   
28                        Dufferin, Dovercourt Village             0.043478   
29                                      Enclave of L4W             0.043478   
30                                      Enclave of M4L             0.043478   
31                                      Enclave of M5E             0.043478   
32   Eringate, Bloordale Gardens, Old Burnhamthorpe...             0.043478   
33                        Fairview, Henry Farm, Oriole             0.043478   
34              First Canadian Place, Underground city             0.043478   
35                            Forest Hill North & West             0.043478   
36                            Garden District, Ryerson             0.043478   
37                                           Glencairn             0.043478   
38                     Golden Mile, Clairlea, Oakridge             0.043478   
39                   Guildwood, Morningside, West Hill             0.043478   
40   Harbourfront East, Union Station, Toronto Islands             0.043478   
41                       High Park, The Junction South             0.043478   
42                                   Hillcrest Village             0.043478   
43                                       Humber Summit             0.043478   
44                                    Humberlea, Emery             0.043478   
45                                  Humewood-Cedarvale             0.043478   
46                      India Bazaar, The Beaches West             0.043478   
47                                    Islington Avenue             0.043478   
48         Kennedy Park, Ionview, East Birchmount Park             0.043478   
49           Kensington Market, Chinatown, Grange Park             0.043478   
50   Kingsvie

In [27]:
toronto_grouped.shape

(103, 22)

###### Let's print each neighborhood along with the top 5 most common venues

In [28]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Alderwood, Long Branch----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Bathurst Manor, Wilson Heights, Downsview North----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Bayview Village----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Bedford Park, Lawrence Manor East----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3        

                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----India Bazaar, The Beaches West----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Islington Avenue----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Kennedy Park, Ionview, East Birchmount Park----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Kensington Market, Chinatown, Grange Park----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             

                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Upper Rouge----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Victoria Village----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Westmount----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Vid

### Let's put that into a pandas dataframe

###### First, let's write a function to sort the venues in descending order.

In [29]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

###### let's create the new dataframe and display the top 12 venues for each neighborhood.

In [30]:
num_top_venues = 20

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt        Sandwich Place   
1                           Alderwood, Long Branch        Sandwich Place   
2  Bathurst Manor, Wilson Heights, Downsview North        Sandwich Place   
3                                  Bayview Village        Sandwich Place   
4                Bedford Park, Lawrence Manor East        Sandwich Place   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                   Gym           Yoga Studio        Ice Cream Shop   
1                   Gym           Yoga Studio        Ice Cream Shop   
2                   Gym           Yoga Studio        Ice Cream Shop   
3                   Gym           Yoga Studio        Ice Cream Shop   
4                   Gym           Yoga Studio        Ice Cream Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Clothing Store           Coffee Shop         Deli / Bodega   
1        Clothing Store           Coffee Shop         Deli / Bodega   
2        Clothing Store           Coffee Shop         Deli / Bodega   
3        Clothing Store           Coffee Shop         Deli / Bodega   
4        Clothing Store           Coffee Shop         Deli / Bodega   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
0      Department Store                 Diner         Discount Store   
1      Department Store                 Diner         Discount Store   
2      Department Store                 Diner         Discount Store   
3      Department Store                 Diner         Discount Store   
4      Department Store                 Diner         Discount Store   

  11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
0             Donut Shop             Kids Store       Video Game Store   
1             Donut Shop             Kids Store       Video Game Store   
2             Donut Shop             Kids Store       Video Game Store   
3             Donut Shop             Kids Store       Video Game Store   
4             Donut Shop             Kids Store       Video Game Store   

  14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
0               Pharmacy            Pizza Place     Seafood Restaurant   
1               Pharmacy            Pizza Place     Seafood Restaurant   
2               Pharmacy            Pizza Place     Seafood Restaurant   
3               Pharmacy            Pizza Place     Seafood Restaurant   
4               Pharmacy            Pizza Place     Seafood Restaurant   

  17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
0          Shopping Mall             Steakhouse        Supplement Shop   
1          Shopping Mall             Steakhouse        Supplement Shop   
2          Shopping Mall             Steakhouse        Supplement Shop   
3          Shopping Mall             Steakhouse        Supplement Shop   
4          Shopping Mall             Steakhouse        Supplement Shop   

  20th Most Common Venue  
0         Tennis Stadium  
1         Tennis Stadium  
2         Tennis Stadium  
3         Tennis Stadium  
4         Tennis Stadium

## 1.4 Cluster Neighborhoods

### Run k-means to cluster the neighborhood into 5 clusters.

In [31]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
#kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)
kmeans = KMeans(init = "k-means++", n_clusters = kclusters, n_init = 12).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

<ipython-input-31-8ad534598560>:8: ConvergenceWarning: Number of distinct clusters (1) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  kmeans = KMeans(init = "k-means++", n_clusters = kclusters, n_init = 12).fit(toronto_grouped_clustering)


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

 Let's create a new dataframe that includes the cluster as well as the top 20 venues for each neighborhood.

In [32]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')



In [33]:
toronto_merged.tail() # check the last columns!

PostalCode                Borough  \
98         M8X              Etobicoke   
99         M4Y       Downtown Toronto   
100        M7Y  East Toronto Business   
101        M8Y              Etobicoke   
102        M8Z              Etobicoke   

                                          Neighborhood   Latitude  Longitude  \
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944   
99                                Church and Wellesley  43.665860 -79.383160   
100                                     Enclave of M4L  43.662744 -79.321558   
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509   
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
98                0        Sandwich Place                   Gym   
99                0        Sandwich Place                   Gym   
100               0        Sandwich Place                   Gym   
101               0        Sandwich Place                   Gym   
102               0        Sandwich Place                   Gym   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
98            Yoga Studio        Ice Cream Shop        Clothing Store   
99            Yoga Studio        Ice Cream Shop        Clothing Store   
100           Yoga Studio        Ice Cream Shop        Clothing Store   
101           Yoga Studio        Ice Cream Shop        Clothing Store   
102           Yoga Studio        Ice Cream Shop        Clothing Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
98            Coffee Shop         Deli / Bodega      Department Store   
99            Coffee Shop         Deli / Bodega      Department Store   
100           Coffee Shop         Deli / Bodega      Department Store   
101           Coffee Shop         Deli / Bodega      Department Store   
102           Coffee Shop         Deli / Bodega      Department Store   

    9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
98                  Diner         Discount Store             Donut Shop   
99                  Diner         Discount Store             Donut Shop   
100                 Diner         Discount Store             Donut Shop   
101                 Diner         Discount Store             Donut Shop   
102                 Diner         Discount Store             Donut Shop   

    12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
98              Kids Store       Video Game Store               Pharmacy   
99              Kids Store       Video Game Store               Pharmacy   
100             Kids Store       Video Game Store               Pharmacy   
101             Kids Store       Video Game Store               Pharmacy   
102             Kids Store       Video Game Store               Pharmacy   

    15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
98             Pizza Place     Seafood Restaurant          Shopping Mall   
99             Pizza Place     Seafood Restaurant          Shopping Mall   
100            Pizza Place     Seafood Restaurant          Shopping Mall   
101            Pizza Place     Seafood Restaurant          Shopping Mall   
102            Pizza Place     Seafood Restaurant          Shopping Mall   

    18th Most Common Venue 19th Most Common Venue 20th Most Common Venue  
98              Steakhouse        Supplement Shop         Tennis Stadium  
99              Steakhouse        Supplement Shop         Tennis Stadium  
100             Steakhouse        Supplement Shop         Tennis Stadium  
101             Steakhouse        Supplement Shop         Tennis Stadium  
102             Steakhouse        Supplement Shop         Tennis Stadium

## Visuzlize the cluster

In [34]:
# create map
latitude = 43.654260
longitude = -79.360636
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-0],
        fill=True,
        fill_color=rainbow[cluster-0],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 1.5. Examine Clustersster

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

###### Cluster 1

In [35]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, 
                   toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0                North York               0        Sandwich Place   
1                North York               0        Sandwich Place   
2          Downtown Toronto               0        Sandwich Place   
3                North York               0        Sandwich Place   
4              Queen's Park               0        Sandwich Place   
5                 Etobicoke               0        Sandwich Place   
6               Scarborough               0        Sandwich Place   
7                North York               0        Sandwich Place   
8                 East York               0        Sandwich Place   
9          Downtown Toronto               0        Sandwich Place   
10               North York               0        Sandwich Place   
11                Etobicoke               0        Sandwich Place   
12              Scarborough               0        Sandwich Place   
13               North York               0        Sandwich Place   
14                East York               0        Sandwich Place   
15         Downtown Toronto               0        Sandwich Place   
16                     York               0        Sandwich Place   
17                Etobicoke               0        Sandwich Place   
18              Scarborough               0        Sandwich Place   
19             East Toronto               0        Sandwich Place   
20         Downtown Toronto               0        Sandwich Place   
21                     York               0        Sandwich Place   
22              Scarborough               0        Sandwich Place   
23                East York               0        Sandwich Place   
24         Downtown Toronto               0        Sandwich Place   
25         Downtown Toronto               0        Sandwich Place   
26              Scarborough               0        Sandwich Place   
27               North York               0        Sandwich Place   
28               North York               0        Sandwich Place   
29                East York               0        Sandwich Place   
30         Downtown Toronto               0        Sandwich Place   
31             West Toronto               0        Sandwich Place   
32              Scarborough               0        Sandwich Place   
33               North York               0        Sandwich Place   
34               North York               0        Sandwich Place   
35   East York/East Toronto               0        Sandwich Place   
36         Downtown Toronto               0        Sandwich Place   
37             West Toronto               0        Sandwich Place   
38              Scarborough               0        Sandwich Place   
39               North York               0        Sandwich Place   
40               North York               0        Sandwich Place   
41             East Toronto               0        Sandwich Place   
42         Downtown Toronto               0        Sandwich Place   
43             West Toronto               0        Sandwich Place   
44              Scarborough               0        Sandwich Place   
45               North York               0        Sandwich Place   
46               North York               0        Sandwich Place   
47             East Toronto               0        Sandwich Place   
48         Downtown Toronto               0        Sandwich Place   
49               North York               0        Sandwich Place   
50               North York               0        Sandwich Place   
51              Scarborough               0        Sandwich Place   
52               North York               0        Sandwich Place   
53               North York               0        Sandwich Place   
54             East Toronto               0        Sandwich Place   
55               North York               0        Sandwich Place   
56                     York               0        Sandwich Place   
57               N

###### Cluster 2

In [36]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, 
                   toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

###### Cluster 3

In [37]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, 
                   toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

In [38]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, 
                   toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

In [39]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, 
                   toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

# 2. New York City

## 2.1 Segmenting and Clustering Neighborhoods 

In [40]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [41]:
neighborhoods_data = newyork_data['features']

In [42]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [43]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [44]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [45]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [46]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [47]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape
    )
)

The dataframe has 5 boroughs and (306, 4) neighborhoods.


## 2.2 Explore and cluster the neighborhoods in Toronto

### 2.2.1. Visulaize all neighborhoods of Borough in New York

In [48]:
latitude = 40.7127281
longitude = -74.0060152
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [49]:
#manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data = neighborhoods

manhattan_data.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

### 2.2.2. Your credentails:

In [50]:
#CLIENT_ID = '1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5' # your Foursquare ID
#CLIENT_SECRET = 'MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE' # your Foursquare Secret
#VERSION = '20210403' # Foursquare API version
#LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5
CLIENT_SECRET:MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE


## 2.3 explore the all neighborhoods

In [51]:
#manhattan_data.loc[0, 'Neighborhood']
manhattan_data.head(1)

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201

In [52]:
# type your answer here 
#Manhattan are 40.7896239, -73.9598939.
#manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'], latitudes=manhattan_data['Latitude'], longitudes=manhattan_data['Longitude'])

manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [53]:
print(manhattan_venues.shape)
manhattan_venues.head()

(7038, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                              Venue  Venue Latitude  Venue Longitude  \
0                          Arturo's       40.874412       -73.910271   
1                       Bikram Yoga       40.876844       -73.906204   
2                     Tibbett Diner       40.880404       -73.908937   
3  Astral Fitness & Wellness Center       40.876705       -73.906372   
4                           Dunkin'       40.877136       -73.906666   

  Venue Category  
0    Pizza Place  
1    Yoga Studio  
2          Diner  
3            Gym  
4     Donut Shop

In [54]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      23                      23   
Annadale                                      23                      23   
Arden Heights                                 23                      23   
Arlington                                     23                      23   
Arrochar                                      23                      23   
Arverne                                       23                      23   
Astoria                                       23                      23   
Astoria Heights                               23                      23   
Auburndale                                    23                      23   
Bath Beach                                    23                      23   
Battery Park City                             23                      23   
Bay Ridge                                     23                      23   
Bay Terrace                                   46                      46   
Baychester                                    23                      23   
Bayside                                       23                      23   
Bayswater                                     23                      23   
Bedford Park                                  23                      23   
Bedford Stuyvesant                            23                      23   
Beechhurst                                    23                      23   
Bellaire                                      23                      23   
Belle Harbor                                  23                      23   
Bellerose                                     23                      23   
Belmont                                       23                      23   
Bensonhurst                                   23                      23   
Bergen Beach                                  23                      23   
Blissville                                    23                      23   
Bloomfield                                    23                      23   
Boerum Hill                                   23                      23   
Borough Park                                  23                      23   
Breezy Point                                  23                      23   
Briarwood                                     23                      23   
Brighton Beach                                23                      23   
Broad Channel                                 23                      23   
Broadway Junction                             23                      23   
Bronxdale                                     23                      23   
Brooklyn Heights                              23                      23   
Brookville                                    23                      23   
Brownsville                                   23                      23   
Bulls Head                                    23                      23   
Bushwick                                      23                      23   
Butler Manor                                  23                      23   
Cambria Heights                               23                      23   
Canarsie                                      23                      23   
Carnegie Hill                                 23                      23   
Carroll Gardens                               23                      23   
Castle Hill                                   23                      23   
Castleton Corners                             23                      23   
Central Harlem                                23                      23   
Charleston                                    23                      23   
Chelsea                                       46                      46   
Chinatown                                     23                      23   

In [55]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 21 uniques categories.


## 2.3.1 Analyze neighborhoods:

In [56]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  American Restaurant  Clothing Store  Coffee Shop  \
0    Wakefield                    0               0            0   
1    Wakefield                    0               0            0   
2    Wakefield                    0               0            0   
3    Wakefield                    0               0            0   
4    Wakefield                    0               0            0   

   Deli / Bodega  Department Store  Diner  Discount Store  Donut Shop  Gym  \
0              0                 0      0               0           0    0   
1              0                 0      0               0           0    0   
2              0                 0      1               0           0    0   
3              0                 0      0               0           0    1   
4              0                 0      0               0           1    0   

   Ice Cream Shop  Kids Store  Pharmacy  Pizza Place  Sandwich Place  \
0               0           0         0            1               0   
1               0           0         0            0               0   
2               0           0         0            0               0   
3               0           0         0            0               0   
4               0           0         0            0               0   

   Seafood Restaurant  Shopping Mall  Steakhouse  Supplement Shop  \
0                   0              0           0                0   
1                   0              0           0                0   
2                   0              0           0                0   
3                   0              0           0                0   
4                   0              0           0                0   

   Tennis Stadium  Video Game Store  Yoga Studio  
0               0                 0            0  
1               0                 0            1  
2               0                 0            0  
3               0                 0            0  
4               0                 0            0

In [57]:
manhattan_onehot.shape

(7038, 22)

###### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [58]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  American Restaurant  Clothing Store  \
0                     Allerton             0.043478        0.043478   
1                     Annadale             0.043478        0.043478   
2                Arden Heights             0.043478        0.043478   
3                    Arlington             0.043478        0.043478   
4                     Arrochar             0.043478        0.043478   
5                      Arverne             0.043478        0.043478   
6                      Astoria             0.043478        0.043478   
7              Astoria Heights             0.043478        0.043478   
8                   Auburndale             0.043478        0.043478   
9                   Bath Beach             0.043478        0.043478   
10           Battery Park City             0.043478        0.043478   
11                   Bay Ridge             0.043478        0.043478   
12                 Bay Terrace             0.043478        0.043478   
13                  Baychester             0.043478        0.043478   
14                     Bayside             0.043478        0.043478   
15                   Bayswater             0.043478        0.043478   
16                Bedford Park             0.043478        0.043478   
17          Bedford Stuyvesant             0.043478        0.043478   
18                  Beechhurst             0.043478        0.043478   
19                    Bellaire             0.043478        0.043478   
20                Belle Harbor             0.043478        0.043478   
21                   Bellerose             0.043478        0.043478   
22                     Belmont             0.043478        0.043478   
23                 Bensonhurst             0.043478        0.043478   
24                Bergen Beach             0.043478        0.043478   
25                  Blissville             0.043478        0.043478   
26                  Bloomfield             0.043478        0.043478   
27                 Boerum Hill             0.043478        0.043478   
28                Borough Park             0.043478        0.043478   
29                Breezy Point             0.043478        0.043478   
30                   Briarwood             0.043478        0.043478   
31              Brighton Beach             0.043478        0.043478   
32               Broad Channel             0.043478        0.043478   
33           Broadway Junction             0.043478        0.043478   
34                   Bronxdale             0.043478        0.043478   
35            Brooklyn Heights             0.043478        0.043478   
36                  Brookville             0.043478        0.043478   
37                 Brownsville             0.043478        0.043478   
38                  Bulls Head             0.043478        0.043478   
39                    Bushwick             0.043478        0.043478   
40                Butler Manor             0.043478        0.043478   
41             Cambria Heights             0.043478        0.043478   
42                    Canarsie             0.043478        0.043478   
43               Carnegie Hill             0.043478        0.043478   
44             Carroll Gardens             0.043478        0.043478   
45                 Castle Hill             0.043478        0.043478   
46           Castleton Corners             0.043478        0.043478   
47              Central Harlem             0.043478        0.043478   
48                  Charleston             0.043478        0.043478   
49                     Chelsea             0.043478        0.043478   
50                   Chinatown             0.043478        0.043478   
51                 City Island             0.043478        0.043478   
52                   City Line             0.043478        0.043478   
53                Civic Center             0.043478        0.043478   
54           Claremont Village             0.043478        0.043478   
55                Clason Point            

In [59]:
manhattan_grouped.shape

(302, 22)

In [60]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Annadale----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Arden Heights----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Arlington----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Arrochar----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Arverne----
             

4     Video Game Store  0.04


----Dyker Heights----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----East Elmhurst----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----East Flatbush----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----East Harlem----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----East New York----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video 

4     Video Game Store  0.04


----Lindenwood----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Little Italy----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Little Neck----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Long Island City----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Longwood----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game S

                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Richmond Town----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Richmond Valley----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Ridgewood----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Riverdale----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Rochdale----
                 venu

4     Video Game Store  0.04


----Windsor Terrace----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Wingate----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Woodhaven----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Woodlawn----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


----Woodrow----
                 venue  freq
0                  Gym  0.09
1       Sandwich Place  0.09
2  American Restaurant  0.04
3             Pharmacy  0.04
4     Video Game Store  0.04


In [61]:
num_top_venues = 20

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton        Sandwich Place                   Gym   
1       Annadale        Sandwich Place                   Gym   
2  Arden Heights        Sandwich Place                   Gym   
3      Arlington        Sandwich Place                   Gym   
4       Arrochar        Sandwich Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Yoga Studio        Ice Cream Shop        Clothing Store   
1           Yoga Studio        Ice Cream Shop        Clothing Store   
2           Yoga Studio        Ice Cream Shop        Clothing Store   
3           Yoga Studio        Ice Cream Shop        Clothing Store   
4           Yoga Studio        Ice Cream Shop        Clothing Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Coffee Shop         Deli / Bodega      Department Store   
1           Coffee Shop         Deli / Bodega      Department Store   
2           Coffee Shop         Deli / Bodega      Department Store   
3           Coffee Shop         Deli / Bodega      Department Store   
4           Coffee Shop         Deli / Bodega      Department Store   

  9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
0                 Diner         Discount Store             Donut Shop   
1                 Diner         Discount Store             Donut Shop   
2                 Diner         Discount Store             Donut Shop   
3                 Diner         Discount Store             Donut Shop   
4                 Diner         Discount Store             Donut Shop   

  12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
0             Kids Store       Video Game Store               Pharmacy   
1             Kids Store       Video Game Store               Pharmacy   
2             Kids Store       Video Game Store               Pharmacy   
3             Kids Store       Video Game Store               Pharmacy   
4             Kids Store       Video Game Store               Pharmacy   

  15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
0            Pizza Place     Seafood Restaurant          Shopping Mall   
1            Pizza Place     Seafood Restaurant          Shopping Mall   
2            Pizza Place     Seafood Restaurant          Shopping Mall   
3            Pizza Place     Seafood Restaurant          Shopping Mall   
4            Pizza Place     Seafood Restaurant          Shopping Mall   

  18th Most Common Venue 19th Most Common Venue 20th Most Common Venue  
0             Steakhouse        Supplement Shop         Tennis Stadium  
1             Steakhouse        Supplement Shop         Tennis Stadium  
2             Steakhouse        Supplement Shop         Tennis Stadium  
3             Steakhouse        Supplement Shop         Tennis Stadium  
4             Steakhouse        Supplement Shop         Tennis Stadium

## 2.3. Cluster Neighborhoods

#### Run k-means to cluster the neighborhood into 5 clusters.

In [62]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

<ipython-input-62-c61702644175>:7: ConvergenceWarning: Number of distinct clusters (1) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 20 venues for each neighborhood.

In [63]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               0   
1   Bronx   Co-op City  40.874294 -73.829939               0   
2   Bronx  Eastchester  40.887556 -73.827806               0   
3   Bronx    Fieldston  40.895437 -73.905643               0   
4   Bronx    Riverdale  40.890834 -73.912585               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place                   Gym           Yoga Studio   
1        Sandwich Place                   Gym           Yoga Studio   
2        Sandwich Place                   Gym           Yoga Studio   
3        Sandwich Place                   Gym           Yoga Studio   
4        Sandwich Place                   Gym           Yoga Studio   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Ice Cream Shop        Clothing Store           Coffee Shop   
1        Ice Cream Shop        Clothing Store           Coffee Shop   
2        Ice Cream Shop        Clothing Store           Coffee Shop   
3        Ice Cream Shop        Clothing Store           Coffee Shop   
4        Ice Cream Shop        Clothing Store           Coffee Shop   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0         Deli / Bodega      Department Store                 Diner   
1         Deli / Bodega      Department Store                 Diner   
2         Deli / Bodega      Department Store                 Diner   
3         Deli / Bodega      Department Store                 Diner   
4         Deli / Bodega      Department Store                 Diner   

  10th Most Common Venue 11th Most Common Venue 12th Most Common Venue  \
0         Discount Store             Donut Shop             Kids Store   
1         Discount Store             Donut Shop             Kids Store   
2         Discount Store             Donut Shop             Kids Store   
3         Discount Store             Donut Shop             Kids Store   
4         Discount Store             Donut Shop             Kids Store   

  13th Most Common Venue 14th Most Common Venue 15th Most Common Venue  \
0       Video Game Store               Pharmacy            Pizza Place   
1       Video Game Store               Pharmacy            Pizza Place   
2       Video Game Store               Pharmacy            Pizza Place   
3       Video Game Store               Pharmacy            Pizza Place   
4       Video Game Store               Pharmacy            Pizza Place   

  16th Most Common Venue 17th Most Common Venue 18th Most Common Venue  \
0     Seafood Restaurant          Shopping Mall             Steakhouse   
1     Seafood Restaurant          Shopping Mall             Steakhouse   
2     Seafood Restaurant          Shopping Mall             Steakhouse   
3     Seafood Restaurant          Shopping Mall             Steakhouse   
4     Seafood Restaurant          Shopping Mall             Steakhouse   

  19th Most Common Venue 20th Most Common Venue  
0        Supplement Shop         Tennis Stadium  
1        Supplement Shop         Tennis Stadium  
2        Supplement Shop         Tennis Stadium  
3        Supplement Shop         Tennis Stadium  
4        Supplement Shop         Tennis Stadium

Visualize the clusters

In [64]:
# create map
latitude = 40.7127281
longitude = -74.0060152
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 2.4. Examine Clusters

examine each cluster and determine the discriminating venue categories that distinguish each cluster.

**Cluster 1**

In [65]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0                    Wakefield        Sandwich Place                   Gym   
1                   Co-op City        Sandwich Place                   Gym   
2                  Eastchester        Sandwich Place                   Gym   
3                    Fieldston        Sandwich Place                   Gym   
4                    Riverdale        Sandwich Place                   Gym   
5                  Kingsbridge        Sandwich Place                   Gym   
6                  Marble Hill        Sandwich Place                   Gym   
7                     Woodlawn        Sandwich Place                   Gym   
8                      Norwood        Sandwich Place                   Gym   
9               Williamsbridge        Sandwich Place                   Gym   
10                  Baychester        Sandwich Place                   Gym   
11              Pelham Parkway        Sandwich Place                   Gym   
12                 City Island        Sandwich Place                   Gym   
13                Bedford Park        Sandwich Place                   Gym   
14          University Heights        Sandwich Place                   Gym   
15              Morris Heights        Sandwich Place                   Gym   
16                     Fordham        Sandwich Place                   Gym   
17                East Tremont        Sandwich Place                   Gym   
18                  West Farms        Sandwich Place                   Gym   
19                High  Bridge        Sandwich Place                   Gym   
20                     Melrose        Sandwich Place                   Gym   
21                  Mott Haven        Sandwich Place                   Gym   
22                 Port Morris        Sandwich Place                   Gym   
23                    Longwood        Sandwich Place                   Gym   
24                 Hunts Point        Sandwich Place                   Gym   
25                  Morrisania        Sandwich Place                   Gym   
26                   Soundview        Sandwich Place                   Gym   
27                Clason Point        Sandwich Place                   Gym   
28                 Throgs Neck        Sandwich Place                   Gym   
29                Country Club        Sandwich Place                   Gym   
30                 Parkchester        Sandwich Place                   Gym   
31          Westchester Square        Sandwich Place                   Gym   
32                    Van Nest        Sandwich Place                   Gym   
33                 Morris Park        Sandwich Place                   Gym   
34                     Belmont        Sandwich Place                   Gym   
35              Spuyten Duyvil        Sandwich Place                   Gym   
36             North Riverdale        Sandwich Place                   Gym   
37                  Pelham Bay        Sandwich Place                   Gym   
38               Schuylerville        Sandwich Place                   Gym   
39              Edgewater Park        Sandwich Place                   Gym   
40                 Castle Hill        Sandwich Place                   Gym   
41                   Olinville        Sandwich Place                   Gym   
42              Pelham Gardens        Sandwich Place                   Gym   
43                   Concourse        Sandwich Place                   Gym   
44                   Unionport        Sandwich Place                   Gym   
45                    Edenwald        Sandwich Place                   Gym   
46                   Bay Ridge        Sandwich Place                   Gym   
47                 Bensonhurst        Sandwich Place                   Gym   
48                 Sunset Park        Sandwich Place                   Gym   
49                  Greenpoint        Sandwich Place                   Gym   
50                   Gravesend        Sa

**Cluster 2**

In [66]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

**Cluster 3**

In [67]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

**Cluster 4**

In [68]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

**Cluster 5**

In [69]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

# 3. Paris

## 3.1 Download, Load, and Explore Dataset

In [70]:
with open('correspondances-code-insee-code-postal.json') as json_data:
    France_data = json.load(json_data)

Let's take a quick look at the data.

In [71]:
France_data

[{'datasetid': 'correspondances-code-insee-code-postal',
  'recordid': '2bf36b38314b6c39dfbcd09225f97fa532b1fc45',
  'fields': {'code_comm': '645',
   'nom_dept': 'ESSONNE',
   'statut': 'Commune simple',
   'z_moyen': 121.0,
   'nom_region': 'ILE-DE-FRANCE',
   'code_reg': '11',
   'insee_com': '91645',
   'code_dept': '91',
   'geo_point_2d': [48.750443119964764, 2.251712972144151],
   'postal_code': '91370',
   'id_geofla': '16275',
   'code_cant': '03',
   'geo_shape': {'type': 'Polygon',
    'coordinates': [[[2.238024349288764, 48.735565859837095],
      [2.226414985434264, 48.75003536744732],
      [2.22450256558849, 48.75882853410981],
      [2.232859032169924, 48.76598806763034],
      [2.250043759055985, 48.761213267519565],
      [2.269288614654887, 48.76063999654954],
      [2.276145972515501, 48.75666127305422],
      [2.283691112862691, 48.748081131389654],
      [2.274517407535147, 48.74072222671912],
      [2.238024349288764, 48.735565859837095]]]},
   'superficie': 999.

define Pandas dataframe

In [72]:
neighborhoods_data = France_data

In [73]:
# define the dataframe columns
#column_names = ['postal_code','Borough', 'nom_dept', 'Neighborhood', 'nom_region', 'Latitude', 'Longitude'] 
column_names = ['postal_code','Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [74]:
neighborhoods.head()

Empty DataFrame
Columns: [postal_code, Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [75]:
for data in neighborhoods_data:
    postalcode = data['fields']['postal_code']
    borough = neighborhood_name = data['fields']['nom_dept'] 
    #nomDept = data['fields']['nom_dept']
    neighborhood_name = data['fields']['nom_comm']
    neighborhood_region = data['fields']['nom_region']
        
    neighborhood_latlon = data['fields']['geo_point_2d']
    neighborhood_lat = neighborhood_latlon[0]
    neighborhood_lon = neighborhood_latlon[1]
    
    neighborhoods = neighborhoods.append({
                                        'postal_code': postalcode,
                                        'Borough': borough,
                                        #'nom_dept': nomDept,
                                        'Neighborhood': neighborhood_name,
                                        #'nom_region': neighborhood_region,
                                        'Latitude': neighborhood_lat,
                                        'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [76]:
neighborhoods.head()

postal_code         Borough          Neighborhood   Latitude  Longitude
0       91370         ESSONNE  VERRIERES-LE-BUISSON  48.750443   2.251713
1       77126  SEINE-ET-MARNE  COURCELLES-EN-BASSEE  48.412561   3.052941
2       91730         ESSONNE             MAUCHAMPS  48.527268   2.197182
3       77400  SEINE-ET-MARNE       LAGNY-SUR-MARNE  48.873070   2.709781
4       94110    VAL-DE-MARNE               ARCUEIL  48.805880   2.333510

In [77]:
neighborhoods.shape

(1300, 5)

In [78]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape
    )
)

The dataframe has 8 boroughs and (1300, 5) neighborhoods.


#### the latitude and longitude values of City Paris.

In [79]:
latitude = 48.876896
longitude = 2.337460
print('The geograpical coordinate of Paris are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Paris are 48.876896, 2.33746.


## 3.2 Create a map of Great Paris Area with neighborhoods superimposed on top.

In [80]:
# create map of New York using latitude and longitude values
map_Great_Paris = folium.Map(location=[latitude, longitude], zoom_start=9)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Great_Paris)  
    
map_Great_Paris

Let's simplify the above map and segment and cluster only the neighborhoods in Paris city. So let's slice the original dataframe and create a new dataframe of the Paris data.

In [81]:
paris_data = neighborhoods[neighborhoods['Borough'] == 'PARIS'].reset_index(drop=True)

In [82]:
paris_data.shape

(20, 5)

Let's get the geographical coordinates of Paris city

In [83]:
latitude = 48.876896
longitude = 2.337460
print('The geograpical coordinate of Paris are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Paris are 48.876896, 2.33746.


Let's visualizat Manhattan the neighborhoods in it.

In [84]:
# create map of Manhattan using latitude and longitude values
map_paris = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, label in zip(paris_data['Latitude'], paris_data['Longitude'], paris_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_paris)  
    
map_paris

#### List Foursquare Credentials and Version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [85]:
paris_data.head(1)

postal_code Borough             Neighborhood   Latitude  Longitude
0       75009   PARIS  PARIS-9E-ARRONDISSEMENT  48.876896    2.33746

Get the neighborhood's latitude and longitude values.

In [86]:
neighborhood_latitude = paris_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = paris_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = paris_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of PARIS-9E-ARRONDISSEMENT are 48.87689616237872, 2.337460241388529.


#### Now, let's get the top 100 venues that are in PARIS-9E-ARRONDISSEMEN within a radius of 500 meters.

In [87]:
# type your answer here
LIMIT=100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id=1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5&client_secret=MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE&v=20210403&ll=48.876896, 2.33746&radius=500&limit=100'.format(CLIENT_ID, CLIENT_SECRET, VERSION, neighborhood_latitude, neighborhood_longitude, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5&client_secret=MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE&v=20210403&ll=48.876896, 2.33746&radius=500&limit=100'

Send GET request and exame the results

In [88]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '6074b7b099491a135ff4a5f8'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Saint Georges',
  'headerFullLocation': 'Saint Georges, Paris',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 150,
  'suggestedBounds': {'ne': {'lat': 48.881396004500004,
    'lng': 2.344289474664099},
   'sw': {'lat': 48.8723959955, 'lng': 2.330630525335901}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4f5f4edbe4b06ca37d7a8910',
       'name': 'RAP',
       'location': {'address': '4 rue Fléchier',
        'lat': 48.876628,
        'lng': 2.339359,
        'labeledLatLngs': [{'label': 'display',
          'lat': 48.876628,
          'lng': 2.3393

Explore nearby venues

In [89]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [90]:
venues = results['response']['groups'][0]['items']
#venues[0]   
nearby_venues = json_normalize(venues) # flatten JSON
#nearby_venues.head()
# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]
#nearby_venues.head()
# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)
nearby_venues.head()
# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-90-d5a1534c7854>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name    categories        lat       lng
0                     RAP  Gourmet Shop  48.876628  2.339359
1     Place Saint-Georges         Plaza  48.878408  2.337575
2              Farine & O        Bakery  48.877209  2.339464
3  Le Bouclier de Bacchus      Wine Bar  48.876834  2.337843
4    La Compagnie du Café          Café  48.877916  2.337997

How many venue returned by Foursqure

In [91]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


## 3.3 Explore Neighborhoods in Paris


#### Now create a function; <br> and run the above function on each neighborhood and create a new dataframe called _paris_venues_.

In [92]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id=1JNUAFGTJW3DQDD5C5DRLICP3FHJEPPDDO1I1XQPYJZB0CQ5&client_secret=MMOEN4INZO1WTWS3HUS13IQ4S5YNO5G4UM404J4WZXYWAEKE&v=20210403&ll=48.876896, 2.33746&radius=500&limit=100'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [93]:
paris_venues = getNearbyVenues(names=paris_data['Neighborhood'],
                                   latitudes=paris_data['Latitude'],
                                   longitudes=paris_data['Longitude']
                                  )

PARIS-9E-ARRONDISSEMENT
PARIS-2E-ARRONDISSEMENT
PARIS-11E-ARRONDISSEMENT
PARIS-3E-ARRONDISSEMENT
PARIS-6E-ARRONDISSEMENT
PARIS-4E-ARRONDISSEMENT
PARIS-10E-ARRONDISSEMENT
PARIS-16E-ARRONDISSEMENT
PARIS-8E-ARRONDISSEMENT
PARIS-13E-ARRONDISSEMENT
PARIS-12E-ARRONDISSEMENT
PARIS-5E-ARRONDISSEMENT
PARIS-19E-ARRONDISSEMENT
PARIS-20E-ARRONDISSEMENT
PARIS-7E-ARRONDISSEMENT
PARIS-18E-ARRONDISSEMENT
PARIS-17E-ARRONDISSEMENT
PARIS-15E-ARRONDISSEMENT
PARIS-1ER-ARRONDISSEMENT
PARIS-14E-ARRONDISSEMENT


Check the size the returned dataframe

In [94]:
print(paris_venues.shape)
paris_venues.head()

(2000, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  PARIS-9E-ARRONDISSEMENT              48.876896                 2.33746   
1  PARIS-9E-ARRONDISSEMENT              48.876896                 2.33746   
2  PARIS-9E-ARRONDISSEMENT              48.876896                 2.33746   
3  PARIS-9E-ARRONDISSEMENT              48.876896                 2.33746   
4  PARIS-9E-ARRONDISSEMENT              48.876896                 2.33746   

                    Venue  Venue Latitude  Venue Longitude Venue Category  
0                     RAP       48.876628         2.339359   Gourmet Shop  
1     Place Saint-Georges       48.878408         2.337575          Plaza  
2              Farine & O       48.877209         2.339464         Bakery  
3  Le Bouclier de Bacchus       48.876834         2.337843       Wine Bar  
4    La Compagnie du Café       48.877916         2.337997           Café

Let's check how many venues were returned for each neighborhood

In [95]:
paris_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                              
PARIS-10E-ARRONDISSEMENT                    100                     100   
PARIS-11E-ARRONDISSEMENT                    100                     100   
PARIS-12E-ARRONDISSEMENT                    100                     100   
PARIS-13E-ARRONDISSEMENT                    100                     100   
PARIS-14E-ARRONDISSEMENT                    100                     100   
PARIS-15E-ARRONDISSEMENT                    100                     100   
PARIS-16E-ARRONDISSEMENT                    100                     100   
PARIS-17E-ARRONDISSEMENT                    100                     100   
PARIS-18E-ARRONDISSEMENT                    100                     100   
PARIS-19E-ARRONDISSEMENT                    100                     100   
PARIS-1ER-ARRONDISSEMENT                    100                     100   
PARIS-20E-ARRONDISSEMENT                    100                     100   
PARIS-2E-ARRONDISSEMENT                     100                     100   
PARIS-3E-ARRONDISSEMENT                     100                     100   
PARIS-4E-ARRONDISSEMENT                     100                     100   
PARIS-5E-ARRONDISSEMENT                     100                     100   
PARIS-6E-ARRONDISSEMENT                     100                     100   
PARIS-7E-ARRONDISSEMENT                     100                     100   
PARIS-8E-ARRONDISSEMENT                     100                     100   
PARIS-9E-ARRONDISSEMENT                     100                     100   

                          Venue  Venue Latitude  Venue Longitude  \
Neighborhood                                                       
PARIS-10E-ARRONDISSEMENT    100             100              100   
PARIS-11E-ARRONDISSEMENT    100             100              100   
PARIS-12E-ARRONDISSEMENT    100             100              100   
PARIS-13E-ARRONDISSEMENT    100             100              100   
PARIS-14E-ARRONDISSEMENT    100             100              100   
PARIS-15E-ARRONDISSEMENT    100             100              100   
PARIS-16E-ARRONDISSEMENT    100             100              100   
PARIS-17E-ARRONDISSEMENT    100             100              100   
PARIS-18E-ARRONDISSEMENT    100             100              100   
PARIS-19E-ARRONDISSEMENT    100             100              100   
PARIS-1ER-ARRONDISSEMENT    100             100              100   
PARIS-20E-ARRONDISSEMENT    100             100              100   
PARIS-2E-ARRONDISSEMENT     100             100              100   
PARIS-3E-ARRONDISSEMENT     100             100              100   
PARIS-4E-ARRONDISSEMENT     100             100              100   
PARIS-5E-ARRONDISSEMENT     100             100              100   
PARIS-6E-ARRONDISSEMENT     100             100              100   
PARIS-7E-ARRONDISSEMENT     100             100              100   
PARIS-8E-ARRONDISSEMENT     100             100              100   
PARIS-9E-ARRONDISSEMENT     100             100              100   

                          Venue Category  
Neighborhood                              
PARIS-10E-ARRONDISSEMENT             100  
PARIS-11E-ARRONDISSEMENT             100  
PARIS-12E-ARRONDISSEMENT             100  
PARIS-13E-ARRONDISSEMENT             100  
PARIS-14E-ARRONDISSEMENT             100  
PARIS-15E-ARRONDISSEMENT             100  
PARIS-16E-ARRONDISSEMENT             100  
PARIS-17E-ARRONDISSEMENT             100  
PARIS-18E-ARRONDISSEMENT             100  
PARIS-19E-ARRONDISSEMENT             100  
PARIS-1ER-ARRONDISSEMENT             100  
PARIS-20E-ARRONDISSEMENT             100  
PARIS-2E-ARRONDISSEMENT              100  
PARIS-3E-ARRONDISSEMENT              100  
PARIS-4E-ARRONDISSEMENT              100  
PARIS-5E-ARRONDISSEMENT              100  
PARIS-6E-ARRONDISSEMENT              100  
PARIS-7E-ARRONDISSEMENT              100  
PARIS-8E-ARRONDISS

#### Let's find out how many unique categories can be curated from all the returned venues

In [96]:
print('There are {} uniques categories.'.format(len(paris_venues['Venue Category'].unique())))

There are 51 uniques categories.


## 3.4 Analyze Each Neighborhood

In [97]:
# one hot encoding
paris_onehot = pd.get_dummies(paris_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
paris_onehot['Neighborhood'] = paris_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [paris_onehot.columns[-1]] + list(paris_onehot.columns[:-1])
paris_onehot = paris_onehot[fixed_columns]

paris_onehot.head()

Neighborhood  African Restaurant  Antique Shop  Bakery  Bar  \
0  PARIS-9E-ARRONDISSEMENT                   0             0       0    0   
1  PARIS-9E-ARRONDISSEMENT                   0             0       0    0   
2  PARIS-9E-ARRONDISSEMENT                   0             0       1    0   
3  PARIS-9E-ARRONDISSEMENT                   0             0       0    0   
4  PARIS-9E-ARRONDISSEMENT                   0             0       0    0   

   Bed & Breakfast  Bistro  Brazilian Restaurant  Breakfast Spot  \
0                0       0                     0               0   
1                0       0                     0               0   
2                0       0                     0               0   
3                0       0                     0               0   
4                0       0                     0               0   

   Burger Joint  Café  Candy Store  Cheese Shop  Chinese Restaurant  \
0             0     0            0            0                   0   
1             0     0            0            0                   0   
2             0     0            0            0                   0   
3             0     0            0            0                   0   
4             0     1            0            0                   0   

   Chocolate Shop  Cocktail Bar  Coffee Shop  Corsican Restaurant  Creperie  \
0               0             0            0                    0         0   
1               0             0            0                    0         0   
2               0             0            0                    0         0   
3               0             0            0                    0         0   
4               0             0            0                    0         0   

   Deli / Bodega  Dessert Shop  Exhibit  Falafel Restaurant  \
0              0             0        0                   0   
1              0             0        0                   0   
2              0             0        0                   0   
3              0             0        0                   0   
4              0             0        0                   0   

   French Restaurant  Gift Shop  Gourmet Shop  Gym / Fitness Center  Hotel  \
0                  0          0             1                     0      0   
1                  0          0             0                     0      0   
2                  0          0             0                     0      0   
3                  0          0             0                     0      0   
4                  0          0             0                     0      0   

   Ice Cream Shop  Italian Restaurant  Japanese Restaurant  Juice Bar  \
0               0                   0                    0          0   
1               0                   0                    0          0   
2               0                   0                    0          0   
3               0                   0                    0          0   
4               0                   0                    0          0   

   Latin American Restaurant  Lounge  Modern European Restaurant  Museum  \
0                          0       0                           0       0   
1                          0       0                           0       0   
2                          0       0                           0       0   
3                          0       0                           0       0   
4                          0       0                           0       0   

   Pizza Place  Plaza  Restaurant  Salad Place  Sandwich Place  \
0            0      0           0            0               0   
1            0      1           0            0               0   
2            0      0           0            0               0   
3            0      0           0            0               0   
4            0      0           0            0               0   

   Scandinavian Restaurant  Seafood Restaurant  Shoe Store  Snack Place  \
0                       

the new datafram size

In [98]:
paris_onehot.shape

(2000, 52)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [99]:
paris_grouped = paris_onehot.groupby('Neighborhood').mean().reset_index()
paris_grouped

Neighborhood  African Restaurant  Antique Shop  Bakery   Bar  \
0   PARIS-10E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
1   PARIS-11E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
2   PARIS-12E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
3   PARIS-13E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
4   PARIS-14E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
5   PARIS-15E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
6   PARIS-16E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
7   PARIS-17E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
8   PARIS-18E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
9   PARIS-19E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
10  PARIS-1ER-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
11  PARIS-20E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
12   PARIS-2E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
13   PARIS-3E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
14   PARIS-4E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
15   PARIS-5E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
16   PARIS-6E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
17   PARIS-7E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
18   PARIS-8E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   
19   PARIS-9E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   

    Bed & Breakfast  Bistro  Brazilian Restaurant  Breakfast Spot  \
0              0.01    0.04                  0.01            0.01   
1              0.01    0.04                  0.01            0.01   
2              0.01    0.04                  0.01            0.01   
3              0.01    0.04                  0.01            0.01   
4              0.01    0.04                  0.01            0.01   
5              0.01    0.04                  0.01            0.01   
6              0.01    0.04                  0.01            0.01   
7              0.01    0.04                  0.01            0.01   
8              0.01    0.04                  0.01            0.01   
9              0.01    0.04                  0.01            0.01   
10             0.01    0.04                  0.01            0.01   
11             0.01    0.04                  0.01            0.01   
12             0.01    0.04                  0.01            0.01   
13             0.01    0.04                  0.01            0.01   
14             0.01    0.04                  0.01            0.01   
15             0.01    0.04                  0.01            0.01   
16             0.01    0.04                  0.01            0.01   
17             0.01    0.04                  0.01            0.01   
18             0.01    0.04                  0.01            0.01   
19             0.01    0.04                  0.01            0.01   

    Burger Joint  Café  Candy Store  Cheese Shop  Chinese Restaurant  \
0           0.01  0.02         0.01         0.01                0.01   
1           0.01  0.02         0.01         0.01                0.01   
2           0.01  0.02         0.01         0.01                0.01   
3           0.01  0.02         0.01         0.01                0.01   
4           0.01  0.02         0.01         0.01                0.01   
5           0.01  0.02         0.01         0.01                0.01   
6           0.01  0.02         0.01         0.01                0.01   
7           0.01  0.02         0.01         0.01                0.01   
8           0.01  0.02         0.01         0.01                0.01   
9           0.01  0.02         0.01         0.01                0.01   
10          0.01  0.02         0.01         0.01                0.01   
11          0.01  0.0

Confirm the new frame size

In [100]:
paris_grouped.shape

(20, 52)

#### Let's print each neighborhood along with the top 5 most common venues

In [101]:
num_top_venues = 5

for hood in paris_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = paris_grouped[paris_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----PARIS-10E-ARRONDISSEMENT----
                 venue  freq
0    French Restaurant  0.18
1                Hotel  0.08
2               Bakery  0.04
3               Bistro  0.04
4  Japanese Restaurant  0.04


----PARIS-11E-ARRONDISSEMENT----
                 venue  freq
0    French Restaurant  0.18
1                Hotel  0.08
2               Bakery  0.04
3               Bistro  0.04
4  Japanese Restaurant  0.04


----PARIS-12E-ARRONDISSEMENT----
                 venue  freq
0    French Restaurant  0.18
1                Hotel  0.08
2               Bakery  0.04
3               Bistro  0.04
4  Japanese Restaurant  0.04


----PARIS-13E-ARRONDISSEMENT----
                 venue  freq
0    French Restaurant  0.18
1                Hotel  0.08
2               Bakery  0.04
3               Bistro  0.04
4  Japanese Restaurant  0.04


----PARIS-14E-ARRONDISSEMENT----
                 venue  freq
0    French Restaurant  0.18
1                Hotel  0.08
2               Bakery  0.04
3              

#### Let's put that into a _pandas_ dataframe

First, let's write a function to sort the venues in descending order.

In [102]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 20 venues for each neighborhood.



In [103]:
num_top_venues = 20

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = paris_grouped['Neighborhood']

for ind in np.arange(paris_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(paris_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  PARIS-10E-ARRONDISSEMENT     French Restaurant                 Hotel   
1  PARIS-11E-ARRONDISSEMENT     French Restaurant                 Hotel   
2  PARIS-12E-ARRONDISSEMENT     French Restaurant                 Hotel   
3  PARIS-13E-ARRONDISSEMENT     French Restaurant                 Hotel   
4  PARIS-14E-ARRONDISSEMENT     French Restaurant                 Hotel   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Bakery                Bistro   Japanese Restaurant   
1                Bakery                Bistro   Japanese Restaurant   
2                Bakery                Bistro   Japanese Restaurant   
3                Bakery                Bistro   Japanese Restaurant   
4                Bakery                Bistro   Japanese Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0              Wine Bar          Cocktail Bar                Lounge   
1              Wine Bar          Cocktail Bar                Lounge   
2              Wine Bar          Cocktail Bar                Lounge   
3              Wine Bar          Cocktail Bar                Lounge   
4              Wine Bar          Cocktail Bar                Lounge   

  9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
0                 Plaza                    Bar                   Café   
1                 Plaza                    Bar                   Café   
2                 Plaza                    Bar                   Café   
3                 Plaza                    Bar                   Café   
4                 Plaza                    Bar                   Café   

  12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
0            Coffee Shop               Creperie            Pizza Place   
1            Coffee Shop               Creperie            Pizza Place   
2            Coffee Shop               Creperie            Pizza Place   
3            Coffee Shop               Creperie            Pizza Place   
4            Coffee Shop               Creperie            Pizza Place   

  15th Most Common Venue 16th Most Common Venue  \
0   Gym / Fitness Center               Tea Room   
1   Gym / Fitness Center               Tea Room   
2   Gym / Fitness Center               Tea Room   
3   Gym / Fitness Center               Tea Room   
4   Gym / Fitness Center               Tea Room   

          17th Most Common Venue 18th Most Common Venue  \
0  Vegetarian / Vegan Restaurant     Turkish Restaurant   
1  Vegetarian / Vegan Restaurant     Turkish Restaurant   
2  Vegetarian / Vegan Restaurant     Turkish Restaurant   
3  Vegetarian / Vegan Restaurant     Turkish Restaurant   
4  Vegetarian / Vegan Restaurant     Turkish Restaurant   

  19th Most Common Venue 20th Most Common Venue  
0             Restaurant                Theater  
1             Restaurant                Theater  
2             Restaurant                Theater  
3             Restaurant                Theater  
4             Restaurant                Theater

## 3.5. Cluster Neighborhoods

Run _k_-means to cluster the neighborhood into 5 clusters.

In [104]:
# set number of clusters
kclusters = 5

paris_grouped_clustering = paris_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(paris_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

<ipython-input-104-453a19415c07>:7: ConvergenceWarning: Number of distinct clusters (1) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(paris_grouped_clustering)


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [105]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

paris_merged = paris_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
paris_merged = paris_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

paris_merged.head() # check the last columns!

postal_code Borough              Neighborhood   Latitude  Longitude  \
0       75009   PARIS   PARIS-9E-ARRONDISSEMENT  48.876896   2.337460   
1       75002   PARIS   PARIS-2E-ARRONDISSEMENT  48.867903   2.344107   
2       75011   PARIS  PARIS-11E-ARRONDISSEMENT  48.859415   2.378741   
3       75003   PARIS   PARIS-3E-ARRONDISSEMENT  48.863054   2.359361   
4       75006   PARIS   PARIS-6E-ARRONDISSEMENT  48.848968   2.332671   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               0     French Restaurant                 Hotel   
1               0     French Restaurant                 Hotel   
2               0     French Restaurant                 Hotel   
3               0     French Restaurant                 Hotel   
4               0     French Restaurant                 Hotel   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Bakery                Bistro   Japanese Restaurant   
1                Bakery                Bistro   Japanese Restaurant   
2                Bakery                Bistro   Japanese Restaurant   
3                Bakery                Bistro   Japanese Restaurant   
4                Bakery                Bistro   Japanese Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0              Wine Bar          Cocktail Bar                Lounge   
1              Wine Bar          Cocktail Bar                Lounge   
2              Wine Bar          Cocktail Bar                Lounge   
3              Wine Bar          Cocktail Bar                Lounge   
4              Wine Bar          Cocktail Bar                Lounge   

  9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
0                 Plaza                    Bar                   Café   
1                 Plaza                    Bar                   Café   
2                 Plaza                    Bar                   Café   
3                 Plaza                    Bar                   Café   
4                 Plaza                    Bar                   Café   

  12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
0            Coffee Shop               Creperie            Pizza Place   
1            Coffee Shop               Creperie            Pizza Place   
2            Coffee Shop               Creperie            Pizza Place   
3            Coffee Shop               Creperie            Pizza Place   
4            Coffee Shop               Creperie            Pizza Place   

  15th Most Common Venue 16th Most Common Venue  \
0   Gym / Fitness Center               Tea Room   
1   Gym / Fitness Center               Tea Room   
2   Gym / Fitness Center               Tea Room   
3   Gym / Fitness Center               Tea Room   
4   Gym / Fitness Center               Tea Room   

          17th Most Common Venue 18th Most Common Venue  \
0  Vegetarian / Vegan Restaurant     Turkish Restaurant   
1  Vegetarian / Vegan Restaurant     Turkish Restaurant   
2  Vegetarian / Vegan Restaurant     Turkish Restaurant   
3  Vegetarian / Vegan Restaurant     Turkish Restaurant   
4  Vegetarian / Vegan Restaurant     Turkish Restaurant   

  19th Most Common Venue 20th Most Common Venue  
0             Restaurant                Theater  
1             Restaurant                Theater  
2             Restaurant                Theater  
3             Restaurant                Theater  
4             Restaurant                Theater

Finally, let's visualize the resulting clusters

In [106]:
# create map
latitude = 48.876896
longitude = 2.337460
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(paris_merged['Latitude'], paris_merged['Longitude'], paris_merged['Neighborhood'], paris_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster+2],
        fill=True,
        fill_color=rainbow[cluster+2],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 3.6. Examine Clusters

Now, examine each cluster and determine the discriminating venue categories that distinguish each cluster.

**Cluster 1**

In [107]:
paris_merged.loc[paris_merged['Cluster Labels'] == 0, paris_merged.columns[[1] + list(range(5, paris_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0    PARIS               0     French Restaurant                 Hotel   
1    PARIS               0     French Restaurant                 Hotel   
2    PARIS               0     French Restaurant                 Hotel   
3    PARIS               0     French Restaurant                 Hotel   
4    PARIS               0     French Restaurant                 Hotel   
5    PARIS               0     French Restaurant                 Hotel   
6    PARIS               0     French Restaurant                 Hotel   
7    PARIS               0     French Restaurant                 Hotel   
8    PARIS               0     French Restaurant                 Hotel   
9    PARIS               0     French Restaurant                 Hotel   
10   PARIS               0     French Restaurant                 Hotel   
11   PARIS               0     French Restaurant                 Hotel   
12   PARIS               0     French Restaurant                 Hotel   
13   PARIS               0     French Restaurant                 Hotel   
14   PARIS               0     French Restaurant                 Hotel   
15   PARIS               0     French Restaurant                 Hotel   
16   PARIS               0     French Restaurant                 Hotel   
17   PARIS               0     French Restaurant                 Hotel   
18   PARIS               0     French Restaurant                 Hotel   
19   PARIS               0     French Restaurant                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                 Bakery                Bistro   Japanese Restaurant   
1                 Bakery                Bistro   Japanese Restaurant   
2                 Bakery                Bistro   Japanese Restaurant   
3                 Bakery                Bistro   Japanese Restaurant   
4                 Bakery                Bistro   Japanese Restaurant   
5                 Bakery                Bistro   Japanese Restaurant   
6                 Bakery                Bistro   Japanese Restaurant   
7                 Bakery                Bistro   Japanese Restaurant   
8                 Bakery                Bistro   Japanese Restaurant   
9                 Bakery                Bistro   Japanese Restaurant   
10                Bakery                Bistro   Japanese Restaurant   
11                Bakery                Bistro   Japanese Restaurant   
12                Bakery                Bistro   Japanese Restaurant   
13                Bakery                Bistro   Japanese Restaurant   
14                Bakery                Bistro   Japanese Restaurant   
15                Bakery                Bistro   Japanese Restaurant   
16                Bakery                Bistro   Japanese Restaurant   
17                Bakery                Bistro   Japanese Restaurant   
18                Bakery                Bistro   Japanese Restaurant   
19                Bakery                Bistro   Japanese Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0               Wine Bar          Cocktail Bar                Lounge   
1               Wine Bar          Cocktail Bar                Lounge   
2               Wine Bar          Cocktail Bar                Lounge   
3               Wine Bar          Cocktail Bar                Lounge   
4               Wine Bar          Cocktail Bar                Lounge   
5               Wine Bar          Cocktail Bar                Lounge   
6               Wine Bar          Cocktail Bar                Lounge   
7               Wine Bar          Cocktail Bar                Lounge   
8               Wine Bar          Cocktail Bar                Lounge   
9               Wine Bar          Cocktail Bar                Lounge   
10              Wine Bar          Cocktail Bar                Lounge   
11              Wine Bar          Cocktail Bar                Lounge   

**Cluster 2**

In [108]:
paris_merged.loc[paris_merged['Cluster Labels'] == 1, paris_merged.columns[[1] + list(range(5, paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

**Cluster 3**

In [109]:
paris_merged.loc[paris_merged['Cluster Labels'] == 2, paris_merged.columns[[1] + list(range(5, paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

**Cluster 4**

In [110]:
paris_merged.loc[paris_merged['Cluster Labels'] == 3, paris_merged.columns[[1] + list(range(5, paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

**Cluster 5**

In [111]:
paris_merged.loc[paris_merged['Cluster Labels'] == 4, paris_merged.columns[[1] + list(range(5, paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

# <font color=blue> 4. Discover similarities and disimilarities between the three cities </font>

In [112]:
manhattan_grouped.head(1)

Neighborhood  American Restaurant  Clothing Store  Coffee Shop  \
0     Allerton             0.043478        0.043478     0.043478   

   Deli / Bodega  Department Store     Diner  Discount Store  Donut Shop  \
0       0.043478          0.043478  0.043478        0.043478    0.043478   

        Gym  Ice Cream Shop  Kids Store  Pharmacy  Pizza Place  \
0  0.086957        0.043478    0.043478  0.043478     0.043478   

   Sandwich Place  Seafood Restaurant  Shopping Mall  Steakhouse  \
0        0.086957            0.043478       0.043478    0.043478   

   Supplement Shop  Tennis Stadium  Video Game Store  Yoga Studio  
0         0.043478        0.043478          0.043478     0.043478

In [113]:
manhattan_grouped.shape

(302, 22)

In [114]:
toronto_grouped.head(1)

Neighborhood  American Restaurant  Clothing Store  Coffee Shop  \
0    Agincourt             0.043478        0.043478     0.043478   

   Deli / Bodega  Department Store     Diner  Discount Store  Donut Shop  \
0       0.043478          0.043478  0.043478        0.043478    0.043478   

        Gym  Ice Cream Shop  Kids Store  Pharmacy  Pizza Place  \
0  0.086957        0.043478    0.043478  0.043478     0.043478   

   Sandwich Place  Seafood Restaurant  Shopping Mall  Steakhouse  \
0        0.086957            0.043478       0.043478    0.043478   

   Supplement Shop  Tennis Stadium  Video Game Store  Yoga Studio  
0         0.043478        0.043478          0.043478     0.043478

In [115]:
toronto_grouped.shape

(103, 22)

In [116]:
paris_grouped.head(1)

Neighborhood  African Restaurant  Antique Shop  Bakery   Bar  \
0  PARIS-10E-ARRONDISSEMENT                0.01          0.01    0.04  0.02   

   Bed & Breakfast  Bistro  Brazilian Restaurant  Breakfast Spot  \
0             0.01    0.04                  0.01            0.01   

   Burger Joint  Café  Candy Store  Cheese Shop  Chinese Restaurant  \
0          0.01  0.02         0.01         0.01                0.01   

   Chocolate Shop  Cocktail Bar  Coffee Shop  Corsican Restaurant  Creperie  \
0            0.01          0.03         0.02                 0.01      0.02   

   Deli / Bodega  Dessert Shop  Exhibit  Falafel Restaurant  \
0           0.01          0.01     0.01                0.01   

   French Restaurant  Gift Shop  Gourmet Shop  Gym / Fitness Center  Hotel  \
0               0.18       0.01          0.01                  0.02   0.08   

   Ice Cream Shop  Italian Restaurant  Japanese Restaurant  Juice Bar  \
0            0.01                0.01                 0.04       0.01   

   Latin American Restaurant  Lounge  Modern European Restaurant  Museum  \
0                       0.01    0.03                        0.01    0.01   

   Pizza Place  Plaza  Restaurant  Salad Place  Sandwich Place  \
0         0.02   0.02        0.01         0.01            0.01   

   Scandinavian Restaurant  Seafood Restaurant  Shoe Store  Snack Place  \
0                     0.01                0.01        0.01         0.01   

   Tea Room  Theater  Turkish Restaurant  Vegetarian / Vegan Restaurant  \
0      0.02     0.01                0.02                           0.02   

   Venezuelan Restaurant  Vietnamese Restaurant  Wine Bar  
0                   0.01                   0.01      0.03

In [117]:
paris_grouped.shape

(20, 52)

## 4.1 Catagories similarities

Compare the number of catagories and similar catagories between the three cities

In [148]:
manhattan_grouped_columns_names = list(manhattan_grouped.columns[:])
print('size of catagories for New York City:',len(manhattan_grouped_columns_names))

size of catagories for New York City: 22


In [149]:
toronto_grouped_columns_names = list(toronto_grouped.columns[:])
print('size of catagories for Toronto:', len(toronto_grouped_columns_names))

size of catagories for Toronto: 22


In [150]:
paris_grouped_columns_names = list(paris_grouped.columns[:])
print('size of catagories for Paris:', len(paris_grouped_columns_names))

size of catagories for Paris: 52


Compare catagories difference between the cities:

In [151]:
paris_grouped_columns_names_set = set(paris_grouped_columns_names)
manhattan_grouped_columns_names_set = set(manhattan_grouped_columns_names)
toronto_grouped_columns_names_set = set(toronto_grouped_columns_names)

In [152]:
common_catagories_NewYork_Toronto_set = manhattan_grouped_columns_names_set.intersection(toronto_grouped_columns_names_set)

In [153]:
print('Does New York City has the same catagories as Toronto? Answer is:', common_catagories_NewYork_Toronto_set == manhattan_grouped_columns_names_set)

Does New York City has the same catagories as Toronto? Answer is: True


In [154]:
common_catagories_three_cities_set = paris_grouped_columns_names_set.intersection(manhattan_grouped_columns_names_set)
print('How many of similar catagories between New York city or Toronto and Paris? the number is:', len(common_catagories_three_cities_set))

How many of similar catagories between New York city or Toronto and Paris? the number is: 7


In [155]:
common_catagories_three_cities = list(common_catagories_three_cities_set)
print('the common catagories between the three cities are:', common_catagories_three_cities)

the common catagories between the three cities are: ['Sandwich Place', 'Pizza Place', 'Deli / Bodega', 'Seafood Restaurant', 'Neighborhood', 'Ice Cream Shop', 'Coffee Shop']


In [156]:
toronto_grouped_for_concat = toronto_grouped[manhattan_grouped_columns_names]
list(toronto_grouped_for_concat.columns)

['Neighborhood',
 'American Restaurant',
 'Clothing Store',
 'Coffee Shop',
 'Deli / Bodega',
 'Department Store',
 'Diner',
 'Discount Store',
 'Donut Shop',
 'Gym',
 'Ice Cream Shop',
 'Kids Store',
 'Pharmacy',
 'Pizza Place',
 'Sandwich Place',
 'Seafood Restaurant',
 'Shopping Mall',
 'Steakhouse',
 'Supplement Shop',
 'Tennis Stadium',
 'Video Game Store',
 'Yoga Studio']

## 4.2 Compare New York city and Toronto 

### 4.2.1 Combine New York City and Toronto for applying k-means to clustering 

In [157]:
manhattan_toronto_grouped_concated = manhattan_grouped.append(toronto_grouped_for_concat, ignore_index=True, sort=False)

In [158]:
manhattan_toronto_grouped_concated.shape

(405, 22)

In [159]:
manhattan_toronto_grouped_concated.head(1)

Neighborhood  American Restaurant  Clothing Store  Coffee Shop  \
0     Allerton             0.043478        0.043478     0.043478   

   Deli / Bodega  Department Store     Diner  Discount Store  Donut Shop  \
0       0.043478          0.043478  0.043478        0.043478    0.043478   

        Gym  Ice Cream Shop  Kids Store  Pharmacy  Pizza Place  \
0  0.086957        0.043478    0.043478  0.043478     0.043478   

   Sandwich Place  Seafood Restaurant  Shopping Mall  Steakhouse  \
0        0.086957            0.043478       0.043478    0.043478   

   Supplement Shop  Tennis Stadium  Video Game Store  Yoga Studio  
0         0.043478        0.043478          0.043478     0.043478

In [160]:
manhattan_data.head(1)

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201

In [161]:
toronto_data.head(1)

PostalCode     Borough Neighborhood   Latitude  Longitude
0        M3A  North York    Parkwoods  43.753259 -79.329656

In [162]:
#manhattan_toronto_data_concated = manhattan_data.append(toronto_data, ignore_index=True, sort=False)
manhattan_toronto_data_concated = manhattan_data.append(toronto_data, ignore_index=True, sort=False)

In [163]:
manhattan_toronto_data_concated.shape

(409, 5)

In [164]:
manhattan_toronto_data_concated.head(1)

Borough Neighborhood   Latitude  Longitude PostalCode
0   Bronx    Wakefield  40.894705 -73.847201        NaN

In [165]:
manhattan_toronto_data_concated.tail(1)

Borough                                       Neighborhood   Latitude  \
408  Etobicoke  Mimico NW, The Queensway West, South of Bloor,...  43.628841   

     Longitude PostalCode  
408 -79.520999        M8Z

In [166]:
reorder_columns = ['PostalCode', 'Borough', 'Neighborhood', 'Latitude', 'Longitude']
reorder_columns

['PostalCode', 'Borough', 'Neighborhood', 'Latitude', 'Longitude']

In [167]:
manhattan_toronto_data_concated_recols = manhattan_toronto_data_concated[reorder_columns]

In [168]:
manhattan_toronto_data_concated_recols.shape

(409, 5)

In [169]:
manhattan_toronto_data_concated_recols.head(1)

PostalCode Borough Neighborhood   Latitude  Longitude
0        NaN   Bronx    Wakefield  40.894705 -73.847201

In [170]:
manhattan_toronto_data_concated_recols.tail(1)

PostalCode    Borough                                       Neighborhood  \
408        M8Z  Etobicoke  Mimico NW, The Queensway West, South of Bloor,...   

      Latitude  Longitude  
408  43.628841 -79.520999

find top 20 common catagories

In [171]:
num_top_venues = 20

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_toronto_grouped_concated['Neighborhood']

for ind in np.arange(manhattan_toronto_grouped_concated.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_toronto_grouped_concated.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton        Sandwich Place                   Gym   
1       Annadale        Sandwich Place                   Gym   
2  Arden Heights        Sandwich Place                   Gym   
3      Arlington        Sandwich Place                   Gym   
4       Arrochar        Sandwich Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Yoga Studio        Ice Cream Shop        Clothing Store   
1           Yoga Studio        Ice Cream Shop        Clothing Store   
2           Yoga Studio        Ice Cream Shop        Clothing Store   
3           Yoga Studio        Ice Cream Shop        Clothing Store   
4           Yoga Studio        Ice Cream Shop        Clothing Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Coffee Shop         Deli / Bodega      Department Store   
1           Coffee Shop         Deli / Bodega      Department Store   
2           Coffee Shop         Deli / Bodega      Department Store   
3           Coffee Shop         Deli / Bodega      Department Store   
4           Coffee Shop         Deli / Bodega      Department Store   

  9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
0                 Diner         Discount Store             Donut Shop   
1                 Diner         Discount Store             Donut Shop   
2                 Diner         Discount Store             Donut Shop   
3                 Diner         Discount Store             Donut Shop   
4                 Diner         Discount Store             Donut Shop   

  12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
0             Kids Store       Video Game Store               Pharmacy   
1             Kids Store       Video Game Store               Pharmacy   
2             Kids Store       Video Game Store               Pharmacy   
3             Kids Store       Video Game Store               Pharmacy   
4             Kids Store       Video Game Store               Pharmacy   

  15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
0            Pizza Place     Seafood Restaurant          Shopping Mall   
1            Pizza Place     Seafood Restaurant          Shopping Mall   
2            Pizza Place     Seafood Restaurant          Shopping Mall   
3            Pizza Place     Seafood Restaurant          Shopping Mall   
4            Pizza Place     Seafood Restaurant          Shopping Mall   

  18th Most Common Venue 19th Most Common Venue 20th Most Common Venue  
0             Steakhouse        Supplement Shop         Tennis Stadium  
1             Steakhouse        Supplement Shop         Tennis Stadium  
2             Steakhouse        Supplement Shop         Tennis Stadium  
3             Steakhouse        Supplement Shop         Tennis Stadium  
4             Steakhouse        Supplement Shop         Tennis Stadium

In [172]:
neighborhoods_venues_sorted.tail()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
400   Willowdale, Newtonbrook        Sandwich Place                   Gym   
401                    Woburn        Sandwich Place                   Gym   
402          Woodbine Heights        Sandwich Place                   Gym   
403           York Mills West        Sandwich Place                   Gym   
404  York Mills, Silver Hills        Sandwich Place                   Gym   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
400           Yoga Studio        Ice Cream Shop        Clothing Store   
401           Yoga Studio        Ice Cream Shop        Clothing Store   
402           Yoga Studio        Ice Cream Shop        Clothing Store   
403           Yoga Studio        Ice Cream Shop        Clothing Store   
404           Yoga Studio        Ice Cream Shop        Clothing Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
400           Coffee Shop         Deli / Bodega      Department Store   
401           Coffee Shop         Deli / Bodega      Department Store   
402           Coffee Shop         Deli / Bodega      Department Store   
403           Coffee Shop         Deli / Bodega      Department Store   
404           Coffee Shop         Deli / Bodega      Department Store   

    9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
400                 Diner         Discount Store             Donut Shop   
401                 Diner         Discount Store             Donut Shop   
402                 Diner         Discount Store             Donut Shop   
403                 Diner         Discount Store             Donut Shop   
404                 Diner         Discount Store             Donut Shop   

    12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
400             Kids Store       Video Game Store               Pharmacy   
401             Kids Store       Video Game Store               Pharmacy   
402             Kids Store       Video Game Store               Pharmacy   
403             Kids Store       Video Game Store               Pharmacy   
404             Kids Store       Video Game Store               Pharmacy   

    15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
400            Pizza Place     Seafood Restaurant          Shopping Mall   
401            Pizza Place     Seafood Restaurant          Shopping Mall   
402            Pizza Place     Seafood Restaurant          Shopping Mall   
403            Pizza Place     Seafood Restaurant          Shopping Mall   
404            Pizza Place     Seafood Restaurant          Shopping Mall   

    18th Most Common Venue 19th Most Common Venue 20th Most Common Venue  
400             Steakhouse        Supplement Shop         Tennis Stadium  
401             Steakhouse        Supplement Shop         Tennis Stadium  
402             Steakhouse        Supplement Shop         Tennis Stadium  
403             Steakhouse        Supplement Shop         Tennis Stadium  
404             Steakhouse        Supplement Shop         Tennis Stadium

### 4.2.2 Apply k-means to clustering combined data of New York and Toronto

In [173]:
# set number of clusters
kclusters = 5

manhattan_toronto_grouped_clustering = manhattan_toronto_grouped_concated.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

<ipython-input-173-4ce0eb0c3976>:7: ConvergenceWarning: Number of distinct clusters (1) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_toronto_grouped_clustering)


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [174]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_toronto_merged = manhattan_toronto_data_concated_recols

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_toronto_merged = manhattan_toronto_data_concated_recols.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_toronto_merged.head() # check the last columns!

PostalCode Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0        NaN   Bronx    Wakefield  40.894705 -73.847201               0   
1        NaN   Bronx   Co-op City  40.874294 -73.829939               0   
2        NaN   Bronx  Eastchester  40.887556 -73.827806               0   
3        NaN   Bronx    Fieldston  40.895437 -73.905643               0   
4        NaN   Bronx    Riverdale  40.890834 -73.912585               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place                   Gym           Yoga Studio   
1        Sandwich Place                   Gym           Yoga Studio   
2        Sandwich Place                   Gym           Yoga Studio   
3        Sandwich Place                   Gym           Yoga Studio   
4        Sandwich Place                   Gym           Yoga Studio   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Ice Cream Shop        Clothing Store           Coffee Shop   
1        Ice Cream Shop        Clothing Store           Coffee Shop   
2        Ice Cream Shop        Clothing Store           Coffee Shop   
3        Ice Cream Shop        Clothing Store           Coffee Shop   
4        Ice Cream Shop        Clothing Store           Coffee Shop   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0         Deli / Bodega      Department Store                 Diner   
1         Deli / Bodega      Department Store                 Diner   
2         Deli / Bodega      Department Store                 Diner   
3         Deli / Bodega      Department Store                 Diner   
4         Deli / Bodega      Department Store                 Diner   

  10th Most Common Venue 11th Most Common Venue 12th Most Common Venue  \
0         Discount Store             Donut Shop             Kids Store   
1         Discount Store             Donut Shop             Kids Store   
2         Discount Store             Donut Shop             Kids Store   
3         Discount Store             Donut Shop             Kids Store   
4         Discount Store             Donut Shop             Kids Store   

  13th Most Common Venue 14th Most Common Venue 15th Most Common Venue  \
0       Video Game Store               Pharmacy            Pizza Place   
1       Video Game Store               Pharmacy            Pizza Place   
2       Video Game Store               Pharmacy            Pizza Place   
3       Video Game Store               Pharmacy            Pizza Place   
4       Video Game Store               Pharmacy            Pizza Place   

  16th Most Common Venue 17th Most Common Venue 18th Most Common Venue  \
0     Seafood Restaurant          Shopping Mall             Steakhouse   
1     Seafood Restaurant          Shopping Mall             Steakhouse   
2     Seafood Restaurant          Shopping Mall             Steakhouse   
3     Seafood Restaurant          Shopping Mall             Steakhouse   
4     Seafood Restaurant          Shopping Mall             Steakhouse   

  19th Most Common Venue 20th Most Common Venue  
0        Supplement Shop         Tennis Stadium  
1        Supplement Shop         Tennis Stadium  
2        Supplement Shop         Tennis Stadium  
3        Supplement Shop         Tennis Stadium  
4        Supplement Shop         Tennis Stadium

In [175]:
manhattan_toronto_merged.tail() # check the last columns!

PostalCode                Borough  \
404        M8X              Etobicoke   
405        M4Y       Downtown Toronto   
406        M7Y  East Toronto Business   
407        M8Y              Etobicoke   
408        M8Z              Etobicoke   

                                          Neighborhood   Latitude  Longitude  \
404      The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944   
405                               Church and Wellesley  43.665860 -79.383160   
406                                     Enclave of M4L  43.662744 -79.321558   
407  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509   
408  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
404               0        Sandwich Place                   Gym   
405               0        Sandwich Place                   Gym   
406               0        Sandwich Place                   Gym   
407               0        Sandwich Place                   Gym   
408               0        Sandwich Place                   Gym   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
404           Yoga Studio        Ice Cream Shop        Clothing Store   
405           Yoga Studio        Ice Cream Shop        Clothing Store   
406           Yoga Studio        Ice Cream Shop        Clothing Store   
407           Yoga Studio        Ice Cream Shop        Clothing Store   
408           Yoga Studio        Ice Cream Shop        Clothing Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
404           Coffee Shop         Deli / Bodega      Department Store   
405           Coffee Shop         Deli / Bodega      Department Store   
406           Coffee Shop         Deli / Bodega      Department Store   
407           Coffee Shop         Deli / Bodega      Department Store   
408           Coffee Shop         Deli / Bodega      Department Store   

    9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
404                 Diner         Discount Store             Donut Shop   
405                 Diner         Discount Store             Donut Shop   
406                 Diner         Discount Store             Donut Shop   
407                 Diner         Discount Store             Donut Shop   
408                 Diner         Discount Store             Donut Shop   

    12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
404             Kids Store       Video Game Store               Pharmacy   
405             Kids Store       Video Game Store               Pharmacy   
406             Kids Store       Video Game Store               Pharmacy   
407             Kids Store       Video Game Store               Pharmacy   
408             Kids Store       Video Game Store               Pharmacy   

    15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
404            Pizza Place     Seafood Restaurant          Shopping Mall   
405            Pizza Place     Seafood Restaurant          Shopping Mall   
406            Pizza Place     Seafood Restaurant          Shopping Mall   
407            Pizza Place     Seafood Restaurant          Shopping Mall   
408            Pizza Place     Seafood Restaurant          Shopping Mall   

    18th Most Common Venue 19th Most Common Venue 20th Most Common Venue  
404             Steakhouse        Supplement Shop         Tennis Stadium  
405             Steakhouse        Supplement Shop         Tennis Stadium  
406             Steakhouse        Supplement Shop         Tennis Stadium  
407             Steakhouse        Supplement Shop         Tennis Stadium  
408             Steakhouse        Supplement Shop         Tennis Stadium

### 4.2.2 Visualize clusters of New York and Toronto

In [178]:
latitude = 40.7127281
longitude = -74.0060152
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=6)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_toronto_merged['Latitude'], manhattan_toronto_merged['Longitude'], manhattan_toronto_merged['Neighborhood'], manhattan_toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-0],
        fill=True,
        fill_color=rainbow[cluster-0],
        fill_opacity=0.6).add_to(map_clusters)
       
map_clusters

### 4.2.3 Exam clustering of New York and Toronto

In [179]:
manhattan_toronto_merged.loc[manhattan_toronto_merged['Cluster Labels'] == 0, manhattan_toronto_merged.columns[[1] + list(range(5, manhattan_toronto_merged.shape[1]))]]


Borough  Cluster Labels 1st Most Common Venue  \
0                     Bronx               0        Sandwich Place   
1                     Bronx               0        Sandwich Place   
2                     Bronx               0        Sandwich Place   
3                     Bronx               0        Sandwich Place   
4                     Bronx               0        Sandwich Place   
5                     Bronx               0        Sandwich Place   
6                 Manhattan               0        Sandwich Place   
7                     Bronx               0        Sandwich Place   
8                     Bronx               0        Sandwich Place   
9                     Bronx               0        Sandwich Place   
10                    Bronx               0        Sandwich Place   
11                    Bronx               0        Sandwich Place   
12                    Bronx               0        Sandwich Place   
13                    Bronx               0        Sandwich Place   
14                    Bronx               0        Sandwich Place   
15                    Bronx               0        Sandwich Place   
16                    Bronx               0        Sandwich Place   
17                    Bronx               0        Sandwich Place   
18                    Bronx               0        Sandwich Place   
19                    Bronx               0        Sandwich Place   
20                    Bronx               0        Sandwich Place   
21                    Bronx               0        Sandwich Place   
22                    Bronx               0        Sandwich Place   
23                    Bronx               0        Sandwich Place   
24                    Bronx               0        Sandwich Place   
25                    Bronx               0        Sandwich Place   
26                    Bronx               0        Sandwich Place   
27                    Bronx               0        Sandwich Place   
28                    Bronx               0        Sandwich Place   
29                    Bronx               0        Sandwich Place   
30                    Bronx               0        Sandwich Place   
31                    Bronx               0        Sandwich Place   
32                    Bronx               0        Sandwich Place   
33                    Bronx               0        Sandwich Place   
34                    Bronx               0        Sandwich Place   
35                    Bronx               0        Sandwich Place   
36                    Bronx               0        Sandwich Place   
37                    Bronx               0        Sandwich Place   
38                    Bronx               0        Sandwich Place   
39                    Bronx               0        Sandwich Place   
40                    Bronx               0        Sandwich Place   
41                    Bronx               0        Sandwich Place   
42                    Bronx               0        Sandwich Place   
43                    Bronx               0        Sandwich Place   
44                    Bronx               0        Sandwich Place   
45                    Bronx               0        Sandwich Place   
46                 Brooklyn               0        Sandwich Place   
47                 Brooklyn               0        Sandwich Place   
48                 Brooklyn               0        Sandwich Place   
49                 Brooklyn               0        Sandwich Place   
50                 Brooklyn               0        Sandwich Place   
51                 Brooklyn               0        Sandwich Place   
52                 Brooklyn               0        Sandwich Place   
53                 Brooklyn               0        Sandwich Place   
54                 Brooklyn               0        Sandwich Place   
55                 Brooklyn               0        Sandwich Place   
56                 Brooklyn               0        Sandwich Place   
57                

In [180]:
manhattan_toronto_merged.loc[manhattan_toronto_merged['Cluster Labels'] == 1, manhattan_toronto_merged.columns[[1] + list(range(5, manhattan_toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

In [181]:
manhattan_toronto_merged.loc[manhattan_toronto_merged['Cluster Labels'] == 2, manhattan_toronto_merged.columns[[1] + list(range(5, manhattan_toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

In [182]:
manhattan_toronto_merged.loc[manhattan_toronto_merged['Cluster Labels'] == 3, manhattan_toronto_merged.columns[[1] + list(range(5, manhattan_toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

In [183]:
manhattan_toronto_merged.loc[manhattan_toronto_merged['Cluster Labels'] == 4, manhattan_toronto_merged.columns[[1] + list(range(5, manhattan_toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Borough, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, 11th Most Common Venue, 12th Most Common Venue, 13th Most Common Venue, 14th Most Common Venue, 15th Most Common Venue, 16th Most Common Venue, 17th Most Common Venue, 18th Most Common Venue, 19th Most Common Venue, 20th Most Common Venue]
Index: []

## 4.3 Compare New York city and Paris

### 4.3.1 Combine ONLY common catagories between New York City and Paris for applying k-means to clustering 

Common catagories:

In [213]:
common_catagories_three_cities.sort()
common_catagories_three_cities

['Coffee Shop',
 'Deli / Bodega',
 'Ice Cream Shop',
 'Neighborhood',
 'Pizza Place',
 'Sandwich Place',
 'Seafood Restaurant']

In [214]:
common_catagories_three_cities.remove('Neighborhood')

In [215]:
common_catagories_three_cities

['Coffee Shop',
 'Deli / Bodega',
 'Ice Cream Shop',
 'Pizza Place',
 'Sandwich Place',
 'Seafood Restaurant']

In [216]:
common_catagories_three_cities.insert(0,'Neighborhood')

In [217]:
common_catagories_three_cities_list_name = common_catagories_three_cities
common_catagories_three_cities_list_name

['Neighborhood',
 'Coffee Shop',
 'Deli / Bodega',
 'Ice Cream Shop',
 'Pizza Place',
 'Sandwich Place',
 'Seafood Restaurant']

Extract common catagories:

In [218]:
manhattan_grouped_for_concat = manhattan_grouped[common_catagories_three_cities_list_name]

In [219]:
manhattan_grouped_for_concat.shape

(302, 7)

In [220]:
manhattan_grouped_for_concat.head()

Neighborhood  Coffee Shop  Deli / Bodega  Ice Cream Shop  Pizza Place  \
0       Allerton     0.043478       0.043478        0.043478     0.043478   
1       Annadale     0.043478       0.043478        0.043478     0.043478   
2  Arden Heights     0.043478       0.043478        0.043478     0.043478   
3      Arlington     0.043478       0.043478        0.043478     0.043478   
4       Arrochar     0.043478       0.043478        0.043478     0.043478   

   Sandwich Place  Seafood Restaurant  
0        0.086957            0.043478  
1        0.086957            0.043478  
2        0.086957            0.043478  
3        0.086957            0.043478  
4        0.086957            0.043478

In [221]:
paris_grouped_for_concat = paris_grouped[common_catagories_three_cities_list_name]

In [222]:
paris_grouped_for_concat.shape

(20, 7)

In [223]:
paris_grouped_for_concat.head()

Neighborhood  Coffee Shop  Deli / Bodega  Ice Cream Shop  \
0  PARIS-10E-ARRONDISSEMENT         0.02           0.01            0.01   
1  PARIS-11E-ARRONDISSEMENT         0.02           0.01            0.01   
2  PARIS-12E-ARRONDISSEMENT         0.02           0.01            0.01   
3  PARIS-13E-ARRONDISSEMENT         0.02           0.01            0.01   
4  PARIS-14E-ARRONDISSEMENT         0.02           0.01            0.01   

   Pizza Place  Sandwich Place  Seafood Restaurant  
0         0.02            0.01                0.01  
1         0.02            0.01                0.01  
2         0.02            0.01                0.01  
3         0.02            0.01                0.01  
4         0.02            0.01                0.01

New data frame for common catagories

In [224]:
manhattan_paris_grouped_common_concated = manhattan_grouped_for_concat.append(paris_grouped_for_concat, ignore_index=True, sort=False)

In [225]:
manhattan_paris_grouped_common_concated.shape

(322, 7)

In [226]:
manhattan_paris_grouped_common_concated.tail()

Neighborhood  Coffee Shop  Deli / Bodega  Ice Cream Shop  \
317  PARIS-5E-ARRONDISSEMENT         0.02           0.01            0.01   
318  PARIS-6E-ARRONDISSEMENT         0.02           0.01            0.01   
319  PARIS-7E-ARRONDISSEMENT         0.02           0.01            0.01   
320  PARIS-8E-ARRONDISSEMENT         0.02           0.01            0.01   
321  PARIS-9E-ARRONDISSEMENT         0.02           0.01            0.01   

     Pizza Place  Sandwich Place  Seafood Restaurant  
317         0.02            0.01                0.01  
318         0.02            0.01                0.01  
319         0.02            0.01                0.01  
320         0.02            0.01                0.01  
321         0.02            0.01                0.01

In [227]:
print(manhattan_data.shape)
manhattan_data.head(1)

(306, 4)


Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201

In [228]:
paris_data_dropped = paris_data.drop(columns = ['postal_code'])

In [229]:
print(paris_data_dropped.shape)
paris_data_dropped.head(1)

(20, 4)


Borough             Neighborhood   Latitude  Longitude
0   PARIS  PARIS-9E-ARRONDISSEMENT  48.876896    2.33746

In [230]:
#manhattan_toronto_data_concated = manhattan_data.append(toronto_data, ignore_index=True, sort=False)
manhattan_paris_data_concated = manhattan_data.append(paris_data_dropped, ignore_index=True, sort=False)

In [231]:
manhattan_paris_data_concated.shape

(326, 4)

In [232]:
manhattan_paris_data_concated.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [233]:
manhattan_paris_data_concated.tail()

Borough              Neighborhood   Latitude  Longitude
321   PARIS  PARIS-18E-ARRONDISSEMENT  48.892735   2.348712
322   PARIS  PARIS-17E-ARRONDISSEMENT  48.887337   2.307486
323   PARIS  PARIS-15E-ARRONDISSEMENT  48.840155   2.293559
324   PARIS  PARIS-1ER-ARRONDISSEMENT  48.862630   2.336293
325   PARIS  PARIS-14E-ARRONDISSEMENT  48.828993   2.327101

### 4.3.2 Apply k-means to clustering combined data of New York and Paris

In [234]:
# set number of clusters
kclusters = 5

manhattan_paris_grouped_common_clustering = manhattan_paris_grouped_common_concated.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_paris_grouped_common_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

<ipython-input-234-ca19aebfce18>:7: ConvergenceWarning: Number of distinct clusters (2) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_paris_grouped_common_clustering)


array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [235]:
# add clustering labels
manhattan_paris_grouped_common_concated.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_paris_merged = manhattan_paris_data_concated

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_paris_merged = manhattan_paris_data_concated.join(manhattan_paris_grouped_common_concated.set_index('Neighborhood'), on='Neighborhood')

manhattan_paris_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  Coffee Shop  \
0   Bronx    Wakefield  40.894705 -73.847201               1     0.043478   
1   Bronx   Co-op City  40.874294 -73.829939               1     0.043478   
2   Bronx  Eastchester  40.887556 -73.827806               1     0.043478   
3   Bronx    Fieldston  40.895437 -73.905643               1     0.043478   
4   Bronx    Riverdale  40.890834 -73.912585               1     0.043478   

   Deli / Bodega  Ice Cream Shop  Pizza Place  Sandwich Place  \
0       0.043478        0.043478     0.043478        0.086957   
1       0.043478        0.043478     0.043478        0.086957   
2       0.043478        0.043478     0.043478        0.086957   
3       0.043478        0.043478     0.043478        0.086957   
4       0.043478        0.043478     0.043478        0.086957   

   Seafood Restaurant  
0            0.043478  
1            0.043478  
2            0.043478  
3            0.043478  
4            0.043478

In [236]:
manhattan_paris_merged.tail()

Borough              Neighborhood   Latitude  Longitude  Cluster Labels  \
321   PARIS  PARIS-18E-ARRONDISSEMENT  48.892735   2.348712               0   
322   PARIS  PARIS-17E-ARRONDISSEMENT  48.887337   2.307486               0   
323   PARIS  PARIS-15E-ARRONDISSEMENT  48.840155   2.293559               0   
324   PARIS  PARIS-1ER-ARRONDISSEMENT  48.862630   2.336293               0   
325   PARIS  PARIS-14E-ARRONDISSEMENT  48.828993   2.327101               0   

     Coffee Shop  Deli / Bodega  Ice Cream Shop  Pizza Place  Sandwich Place  \
321         0.02           0.01            0.01         0.02            0.01   
322         0.02           0.01            0.01         0.02            0.01   
323         0.02           0.01            0.01         0.02            0.01   
324         0.02           0.01            0.01         0.02            0.01   
325         0.02           0.01            0.01         0.02            0.01   

     Seafood Restaurant  
321                0.01  
322                0.01  
323                0.01  
324                0.01  
325                0.01

### 4.3.3 Visualize clusters of New York and Paris

In [237]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=2)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_paris_merged['Latitude'], manhattan_paris_merged['Longitude'], manhattan_toronto_merged['Neighborhood'], manhattan_paris_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.6).add_to(map_clusters)
       
map_clusters

### 4.3.4 Exam clustering of New York and Toronto


**Cluster 1 - Paris**

In [238]:
manhattan_paris_merged.loc[manhattan_paris_merged['Cluster Labels'] == 0, manhattan_paris_merged.columns[[1] + list(range(5, manhattan_paris_merged.shape[1]))]]

Neighborhood  Coffee Shop  Deli / Bodega  Ice Cream Shop  \
306   PARIS-9E-ARRONDISSEMENT         0.02           0.01            0.01   
307   PARIS-2E-ARRONDISSEMENT         0.02           0.01            0.01   
308  PARIS-11E-ARRONDISSEMENT         0.02           0.01            0.01   
309   PARIS-3E-ARRONDISSEMENT         0.02           0.01            0.01   
310   PARIS-6E-ARRONDISSEMENT         0.02           0.01            0.01   
311   PARIS-4E-ARRONDISSEMENT         0.02           0.01            0.01   
312  PARIS-10E-ARRONDISSEMENT         0.02           0.01            0.01   
313  PARIS-16E-ARRONDISSEMENT         0.02           0.01            0.01   
314   PARIS-8E-ARRONDISSEMENT         0.02           0.01            0.01   
315  PARIS-13E-ARRONDISSEMENT         0.02           0.01            0.01   
316  PARIS-12E-ARRONDISSEMENT         0.02           0.01            0.01   
317   PARIS-5E-ARRONDISSEMENT         0.02           0.01            0.01   
318  PARIS-19E-ARRONDISSEMENT         0.02           0.01            0.01   
319  PARIS-20E-ARRONDISSEMENT         0.02           0.01            0.01   
320   PARIS-7E-ARRONDISSEMENT         0.02           0.01            0.01   
321  PARIS-18E-ARRONDISSEMENT         0.02           0.01            0.01   
322  PARIS-17E-ARRONDISSEMENT         0.02           0.01            0.01   
323  PARIS-15E-ARRONDISSEMENT         0.02           0.01            0.01   
324  PARIS-1ER-ARRONDISSEMENT         0.02           0.01            0.01   
325  PARIS-14E-ARRONDISSEMENT         0.02           0.01            0.01   

     Pizza Place  Sandwich Place  Seafood Restaurant  
306         0.02            0.01                0.01  
307         0.02            0.01                0.01  
308         0.02            0.01                0.01  
309         0.02            0.01                0.01  
310         0.02            0.01                0.01  
311         0.02            0.01                0.01  
312         0.02            0.01                0.01  
313         0.02            0.01                0.01  
314         0.02            0.01                0.01  
315         0.02            0.01                0.01  
316         0.02            0.01                0.01  
317         0.02            0.01                0.01  
318         0.02            0.01                0.01  
319         0.02            0.01                0.01  
320         0.02            0.01                0.01  
321         0.02            0.01                0.01  
322         0.02            0.01                0.01  
323         0.02            0.01                0.01  
324         0.02            0.01                0.01  
325         0.02            0.01                0.01

**Cluster 2 - New York City**

In [239]:
manhattan_paris_merged.loc[manhattan_paris_merged['Cluster Labels'] == 1, manhattan_paris_merged.columns[[1] + list(range(5, manhattan_paris_merged.shape[1]))]]

Neighborhood  Coffee Shop  Deli / Bodega  Ice Cream Shop  \
0                    Wakefield     0.043478       0.043478        0.043478   
1                   Co-op City     0.043478       0.043478        0.043478   
2                  Eastchester     0.043478       0.043478        0.043478   
3                    Fieldston     0.043478       0.043478        0.043478   
4                    Riverdale     0.043478       0.043478        0.043478   
5                  Kingsbridge     0.043478       0.043478        0.043478   
6                  Marble Hill     0.043478       0.043478        0.043478   
7                     Woodlawn     0.043478       0.043478        0.043478   
8                      Norwood     0.043478       0.043478        0.043478   
9               Williamsbridge     0.043478       0.043478        0.043478   
10                  Baychester     0.043478       0.043478        0.043478   
11              Pelham Parkway     0.043478       0.043478        0.043478   
12                 City Island     0.043478       0.043478        0.043478   
13                Bedford Park     0.043478       0.043478        0.043478   
14          University Heights     0.043478       0.043478        0.043478   
15              Morris Heights     0.043478       0.043478        0.043478   
16                     Fordham     0.043478       0.043478        0.043478   
17                East Tremont     0.043478       0.043478        0.043478   
18                  West Farms     0.043478       0.043478        0.043478   
19                High  Bridge     0.043478       0.043478        0.043478   
20                     Melrose     0.043478       0.043478        0.043478   
21                  Mott Haven     0.043478       0.043478        0.043478   
22                 Port Morris     0.043478       0.043478        0.043478   
23                    Longwood     0.043478       0.043478        0.043478   
24                 Hunts Point     0.043478       0.043478        0.043478   
25                  Morrisania     0.043478       0.043478        0.043478   
26                   Soundview     0.043478       0.043478        0.043478   
27                Clason Point     0.043478       0.043478        0.043478   
28                 Throgs Neck     0.043478       0.043478        0.043478   
29                Country Club     0.043478       0.043478        0.043478   
30                 Parkchester     0.043478       0.043478        0.043478   
31          Westchester Square     0.043478       0.043478        0.043478   
32                    Van Nest     0.043478       0.043478        0.043478   
33                 Morris Park     0.043478       0.043478        0.043478   
34                     Belmont     0.043478       0.043478        0.043478   
35              Spuyten Duyvil     0.043478       0.043478        0.043478   
36             North Riverdale     0.043478       0.043478        0.043478   
37                  Pelham Bay     0.043478       0.043478        0.043478   
38               Schuylerville     0.043478       0.043478        0.043478   
39              Edgewater Park     0.043478       0.043478        0.043478   
40                 Castle Hill     0.043478       0.043478        0.043478   
41                   Olinville     0.043478       0.043478        0.043478   
42              Pelham Gardens     0.043478       0.043478        0.043478   
43                   Concourse     0.043478       0.043478        0.043478   
44                   Unionport     0.043478       0.043478        0.043478   
45                    Edenwald     0.043478       0.043478        0.043478   
46                   Bay Ridge     0.043478       0.043478        0.043478   
47                 Bensonhurst     0.043478       0.043478        0.043478   
48                 Sunset Park     0.043478       0.043478        0.043478   
49                  Greenpoint     0.043478       0.043478        0.043478   
50                   Gravesend     0.043

**Cluster 3**

In [240]:
manhattan_paris_merged.loc[manhattan_paris_merged['Cluster Labels'] == 2, manhattan_paris_merged.columns[[1] + list(range(5, manhattan_paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, Coffee Shop, Deli / Bodega, Ice Cream Shop, Pizza Place, Sandwich Place, Seafood Restaurant]
Index: []

**Cluster 4**

In [241]:
manhattan_paris_merged.loc[manhattan_paris_merged['Cluster Labels'] == 3, manhattan_paris_merged.columns[[1] + list(range(5, manhattan_paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, Coffee Shop, Deli / Bodega, Ice Cream Shop, Pizza Place, Sandwich Place, Seafood Restaurant]
Index: []

**Cluster 5**

In [242]:
manhattan_paris_merged.loc[manhattan_paris_merged['Cluster Labels'] == 3, manhattan_paris_merged.columns[[1] + list(range(5, manhattan_paris_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, Coffee Shop, Deli / Bodega, Ice Cream Shop, Pizza Place, Sandwich Place, Seafood Restaurant]
Index: []